# Subharmonic tension intervals

Here we divide three to four parts. Due to equation21 having a denominator with very small numbers, and their figure says as it approximates 0 return 0, we then need to  consider, which 10**(-exp) we need to use.
 - We are going to compute for 32 periods different correlations for each period for each threshold. 
- Then we average the correlations to choose best performing threshold on average

In [8]:
import os
import sys
from pathlib import Path

sys.path.append(str(Path().cwd().parent))

sys.path.append(str(Path().cwd().parent.parent))



In [9]:
import psychoacoustic_tension_chan_module.subharmonic_module as shm
import psychoacoustic_tension_chan_module.interharmonic_module as ihm
import pandas as pd

import altair as alt
import numpy as np

from scipy import stats



In [10]:
## adding column for delta t focused methods vs t sub focused methods vs delta_t/t_sub focused methods
def add_method_focus_column(df_to_change):
    df_to_change['method_focus'] = df_to_change['clean_subharmonic_method'].replace({
        'Method A': 'Delta_t focused',
        'Method B': 'Delta_t focused',
        'Method C': 'Delta_t focused',
        'Method D': 'T_sub focused',
        'Method E': 'T_sub focused',
        'Method F': 'T_sub focused',
        'Method G': 'Delta_t/T_sub focused',
        "Method H": 'Delta_t/T_sub focused',
        'Method I': 'Delta_t/T_sub focused',
        # 'Method C': 'T_sub focused',
    })
    return df_to_change

In [11]:
def clean_subharmonic_method_names(df_to_change):


    # ## fix if error 
    # df_to_change.loc[df_to_change['subharmonic_method'] == 'Smallest_delta_t_and_choose_top_3_t_sub']['subharmonic_method']= "Smallest_delta_t_and_choose_top_3_delta_t"
    # df_to_change.loc[df_to_change['subharmonic_method'] == 'Smallest_t_sub_and_choose_top_3_delta_t']['subharmonic_method']= "Smallest_t_sub_and_choose_top_3_t_sub"
    
    # # df_to_change.at['']Smallest_ratio_and_filter_by_smallest_ratio
    df_to_change['clean_subharmonic_method'] = df_to_change['subharmonic_method'].replace({
        
        'Smallest_delta_t_and_filter_by_smallest_t_sub_(Chan\'s_method?)': 'Method A',
        'Smallest_delta_t_and_choose_top_3_delta_t': 'Method B',
        'Smallest_delta_t_and_filter_by_smallest_ratio': 'Method C',

        'Smallest_t_sub_and_choose_top_3_t_sub': 'Method D',
        'Smallest_t_sub_and_filter_by_smallest_delta_t': 'Method E',
        'Smallest_t_sub_and_filter_by_smallest_ratio': 'Method F',

        'Smallest_ratio_and_filter_by_smallest_t_sub': 'Method G',
        "Smallest_ratio_and_filter_by_smallest_delta_t": 'Method H',
        'Smallest_ratio_and_choose_top_3_ratio': 'Method I',
        'Smallest_ratio_and_filter_by_smallest_ratio': 'Method I',
        # "Smallest_ratio_and_choose_top_3_ratio_without_square": 'Method F_2',
        
        # "Smallest_ratio_and_filter_by_smallest_delta_t_without_square": 'Method G_2',

    })
    return df_to_change


# Ground Truth


In [12]:

## Do intervals!

notes = ['G2','G#2','A2','A#2','B2','C3','C#3','D3','D#3','E3','F3','F#3','G3']

## generating intervals
intervals = []
for note in notes:
    intervals.append(['G2',note])

chord_labels_intervals = ['U', 'm2', 'M2', 'm3', 'M3', 'P4', 'TT', 'P5', 'm6', 'M6', 'm7', 'M7', '8v']

empirical_ranking_intervals = ['U','8v','P5','P4','M3','M6','m6','m3','TT','m7','M2','M7','m2']


## Triads to consider

triads=[
    # major
    ['C4', 'E4', 'G4'],
    ['C4', 'D#4','G#4'],
    ['C4', 'F4', 'A4'],
    #minor
    ['C4', 'D#4','G4'],
    ['C4', 'E4', 'A4'],
    ['C4', 'F4','G#4'],
    #Suspended
    ['C4', 'F4','G4'],
    ['C4', 'D4','G4'],
    ['C4', 'F4','A#4'],
    # Diminished,
    ['C4', 'D#4','F#4'],
    ['C4', 'D#4','A4'],
    ['C4', 'F#4','A4'],
    # augmented
    ['C4', 'E4','G#4'],
]
chord_labels_triads = ['CM', 'G#M1st', 'FM2nd', 'Cm', 'Am1st', 'Fm2nd', 'Csus4','Csus2', 'Fsus42nd', 'Cdim','Adim1st', 'F#dim2nd', 'CAug']
empirical_ranking_triads = ['CM', 'Cm', 'FM2nd', 'Fsus42nd', 'G#M1st','Csus2','Csus4', 'Fm2nd','Adim1st','Am1st', 'F#dim2nd','Cdim', 'CAug' ]
empirical_ranking_nums_triads = [1.667,2.407,2.741,2.852,2.889,3.111,3.148,3.481,3.519,3.593,3.667,3.889,5.259]


periods_considered = [4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32]
threshold_exponents = [1,2,3,4,5,6,7,8,9,10,11,12]

In [13]:



def pipeline_for_subharmonic_normalized_tension_score(notes_to_consider, chord_labels,periods_considered, threshold_exponent_to_apply=3):

    ## we define periods to  consider



    subharmonic_per_period = pd.DataFrame()

    for p in periods_considered:
        all_notes_subharmonic_tension = shm.compute_subharmonic_tension_for_each_note_array(notes_to_consider,chord_labels,periods_considered=p,threshold_neg_exp_for_equation_21=threshold_exponent_to_apply)
        all_notes_subharmonic_tension = shm.compute_normalized_subharmonic_tension_for_each_case(all_notes_subharmonic_tension)

        all_notes_subharmonic_tension['periods_considered']=p
        
        # print(all_notes_subharmonic_tension)

        subharmonic_per_period = pd.concat([subharmonic_per_period,all_notes_subharmonic_tension],ignore_index=False)
    return subharmonic_per_period


        

## Now compute for each threshold considered

In [7]:
def pipeline_for_threshold_considered(notes_to_consider,chord_labels,threshold_exponents,periods_considered):
    subharmonic_per_threshold = pd.DataFrame()

    for threshold in threshold_exponents:
        print(f'Now processing threshold exponent {threshold}')
        
        df_for_threshold = pipeline_for_subharmonic_normalized_tension_score(notes_to_consider=notes_to_consider,chord_labels=chord_labels,periods_considered=periods_considered,threshold_exponent_to_apply=threshold)
        df_for_threshold['threshold_exponent'] = "10**" + str(threshold)

        subharmonic_per_threshold = pd.concat([subharmonic_per_threshold,df_for_threshold],ignore_index=False)
    return subharmonic_per_threshold        
    

In [8]:
interval_subharmonic_w_threshholds = pipeline_for_threshold_considered(notes_to_consider=intervals,chord_labels=chord_labels_intervals,threshold_exponents=threshold_exponents,periods_considered=periods_considered)
interval_subharmonic_w_threshholds

Now processing threshold exponent 1
Now processing threshold exponent 2
Now processing threshold exponent 3
Now processing threshold exponent 4
Now processing threshold exponent 5
Now processing threshold exponent 6
Now processing threshold exponent 7
Now processing threshold exponent 8
Now processing threshold exponent 9
Now processing threshold exponent 10
Now processing threshold exponent 11
Now processing threshold exponent 12


t_values  mean_t_sub       indices  \
0    [0.010204200439176117, 0.010204200439176117]    0.010204    [0.0, 0.0]   
1    [0.020408400878352235, 0.020408400878352235]    0.020408    [1.0, 1.0]   
2    [0.030612601317528354, 0.030612601317528354]    0.030613    [2.0, 2.0]   
3    [0.010204200439176117, 0.010204200439176117]    0.010204    [0.0, 0.0]   
4    [0.020408400878352235, 0.020408400878352235]    0.020408    [1.0, 1.0]   
..                                            ...         ...           ...   
346   [0.06122520263505671, 0.061225202635056715]    0.061225   [5.0, 11.0]   
347    [0.12245040527011342, 0.12245040527011343]    0.122450  [11.0, 23.0]   
348  [0.030612601317528354, 0.030612601317528357]    0.030613    [2.0, 5.0]   
349   [0.06122520263505671, 0.061225202635056715]    0.061225   [5.0, 11.0]   
350    [0.12245040527011342, 0.12245040527011343]    0.122450  [11.0, 23.0]   

     difference_(delta_t)  difference_ratio_(delta_t_hat)  \
0            0.000000e+00                    0.000000e+00   
1            0.000000e+00                    0.000000e+00   
2            0.000000e+00                    0.000000e+00   
3            0.000000e+00                    0.000000e+00   
4            0.000000e+00                    0.000000e+00   
..                    ...                             ...   
346          6.938894e-18                    1.133339e-16   
347          1.387779e-17                    1.133339e-16   
348          3.469447e-18                    1.133339e-16   
349          6.938894e-18                    1.133339e-16   
350          1.387779e-17                    1.133339e-16   

                                                  case  tension_score  \
0    Smallest_delta_t_and_filter_by_smallest_t_sub_...            0.0   
1    Smallest_delta_t_and_filter_by_smallest_t_sub_...            0.0   
2    Smallest_delta_t_and_filter_by_smallest_t_sub_...            0.0   
3            Smallest_delta_t_and_choose_top_3_delta_t            0.0   
4            Smallest_delta_t_and_choose_top_3_delta_t            0.0   
..                                                 ...            ...   
346      Smallest_ratio_and_filter_by_smallest_delta_t            0.0   
347      Smallest_ratio_and_filter_by_smallest_delta_t            0.0   
348              Smallest_ratio_and_choose_top_3_ratio            0.0   
349              Smallest_ratio_and_choose_top_3_ratio            0.0   
350              Smallest_ratio_and_choose_top_3_ratio            0.0   

    note_names chord_label  normalized_tension_score  periods_considered  \
0        G2,G2           U                       0.0                   4   
1        G2,G2           U                       0.0                   4   
2        G2,G2           U                       0.0                   4   
3        G2,G2           U                       0.0                   4   
4        G2,G2           U                       0.0                   4   
..         ...         ...                       ...                 ...   
346      G2,G3          8v                       0.0                  32   
347      G2,G3          8v                       0.0                  32   
348      G2,G3          8v                       0.0                  32   
349      G2,G3          8v                       0.0                  32   
350      G2,G3          8v                       0.0                  32   

    threshold_exponent  
0                10**1  
1                10**1  
2                10**1  
3                10**1  
4                10**1  
..                 ...  
346             10**12  
347             10**12  
348             10**12  
349             10**12  
350             10**12  

[122148 rows x 12 columns]

NOw we have a particular df, that contains the top_n elements from equation 21, for each case for each notes. So if top_n is 3 then we have for each note we have 6* 3 cases, 6 * 3 tension scores, 6 * 3 normalized_tension score. 

So we have to group each case and notes. Then each case will contain every note, and tension scores. 

In [9]:
interval_subharmonic_w_threshholds.to_csv('../data_csvs/interval_subharmonic_w_threshholds.csv')


In [10]:
## first clean the top_m things

grouped_df = interval_subharmonic_w_threshholds.drop(['t_values','mean_t_sub','indices', 'difference_(delta_t)', 'difference_ratio_(delta_t_hat)'], axis=1)
grouped_df = grouped_df.groupby(['case','note_names','periods_considered','threshold_exponent']).first().reset_index()
grouped_df

case note_names  \
0        Smallest_delta_t_and_choose_top_3_delta_t     G2,A#2   
1        Smallest_delta_t_and_choose_top_3_delta_t     G2,A#2   
2        Smallest_delta_t_and_choose_top_3_delta_t     G2,A#2   
3        Smallest_delta_t_and_choose_top_3_delta_t     G2,A#2   
4        Smallest_delta_t_and_choose_top_3_delta_t     G2,A#2   
...                                            ...        ...   
40711  Smallest_t_sub_and_filter_by_smallest_ratio      G2,G3   
40712  Smallest_t_sub_and_filter_by_smallest_ratio      G2,G3   
40713  Smallest_t_sub_and_filter_by_smallest_ratio      G2,G3   
40714  Smallest_t_sub_and_filter_by_smallest_ratio      G2,G3   
40715  Smallest_t_sub_and_filter_by_smallest_ratio      G2,G3   

       periods_considered threshold_exponent  tension_score chord_label  \
0                       4              10**1       0.000000          m3   
1                       4             10**10    9019.475174          m3   
2                       4             10**11    9019.475174          m3   
3                       4             10**12    9019.475174          m3   
4                       4              10**2       0.000000          m3   
...                   ...                ...            ...         ...   
40711                  32              10**5    7478.394594          8v   
40712                  32              10**6    7478.394594          8v   
40713                  32              10**7    7478.394594          8v   
40714                  32              10**8    7478.394594          8v   
40715                  32              10**9    7478.394594          8v   

       normalized_tension_score  
0                      0.000000  
1                      0.158009  
2                      0.158009  
3                      0.158009  
4                      0.000000  
...                         ...  
40711                  0.131012  
40712                  0.131012  
40713                  0.131012  
40714                  0.131012  
40715                  0.131012  

[40716 rows x 7 columns]

In [11]:
## now save csv with scores

grouped_df.to_csv('../data_csvs/overall_subharmonic_tension_intervals_with_tension_score_normalized_per_period_per_threshold.csv')

12 threshholds * 6 cases * 13 intervals * 29 periods = 27,144


In [12]:
grouped_df = pd.read_csv('../data_csvs/overall_subharmonic_tension_intervals_with_tension_score_normalized_per_period_per_threshold.csv',)
grouped_df.drop(['Unnamed: 0'], axis=1, inplace=True)
grouped_df

case note_names  \
0        Smallest_delta_t_and_choose_top_3_delta_t     G2,A#2   
1        Smallest_delta_t_and_choose_top_3_delta_t     G2,A#2   
2        Smallest_delta_t_and_choose_top_3_delta_t     G2,A#2   
3        Smallest_delta_t_and_choose_top_3_delta_t     G2,A#2   
4        Smallest_delta_t_and_choose_top_3_delta_t     G2,A#2   
...                                            ...        ...   
40711  Smallest_t_sub_and_filter_by_smallest_ratio      G2,G3   
40712  Smallest_t_sub_and_filter_by_smallest_ratio      G2,G3   
40713  Smallest_t_sub_and_filter_by_smallest_ratio      G2,G3   
40714  Smallest_t_sub_and_filter_by_smallest_ratio      G2,G3   
40715  Smallest_t_sub_and_filter_by_smallest_ratio      G2,G3   

       periods_considered threshold_exponent  tension_score chord_label  \
0                       4              10**1       0.000000          m3   
1                       4             10**10    9019.475174          m3   
2                       4             10**11    9019.475174          m3   
3                       4             10**12    9019.475174          m3   
4                       4              10**2       0.000000          m3   
...                   ...                ...            ...         ...   
40711                  32              10**5    7478.394594          8v   
40712                  32              10**6    7478.394594          8v   
40713                  32              10**7    7478.394594          8v   
40714                  32              10**8    7478.394594          8v   
40715                  32              10**9    7478.394594          8v   

       normalized_tension_score  
0                      0.000000  
1                      0.158009  
2                      0.158009  
3                      0.158009  
4                      0.000000  
...                         ...  
40711                  0.131012  
40712                  0.131012  
40713                  0.131012  
40714                  0.131012  
40715                  0.131012  

[40716 rows x 7 columns]

## linechart of average correlation per threshold

After computing all possible thresholds and tension scores, we should now average each correlationand plot a linechart, to see, for each case (color) what is the average correlation (y axis) given threshold (x axis)

### Now we are going to create a correlation df

In [13]:
new_df = pd.DataFrame()

def create_corr_df_for_subharmonic_periods_cases(subharmonic_df, 
                                   empirical_ranking=[],
                                   empirical_ranking_num=None,
                                   labels_to_compare_with_rank='chord_labels', 
                                   column_to_compare_with_rank='normalized_tension_score',
                                   break_into_methods='case',
                                   periods='periods_considered'):
    
    ## we create a correlation df using the empirical ranking and the subharmonic df provided
    ## this function creates a correlation dataframe using the rank for a period and a case
    

    for_all_corr_df = pd.DataFrame()

    ## now divide for each period
    for p_case in subharmonic_df[periods].unique():
        period_df = subharmonic_df[subharmonic_df[periods]==p_case]
        # print(period_df.shape)

        ## after period divide for each case
        for method in period_df[break_into_methods].unique():
            methods_in_period_df = period_df[period_df[break_into_methods]==method]

            correlation, p_value, scores_for_each_chord_based_on_emp = shm.get_correlation_between_empirical_and_method(empirical_ranking=empirical_ranking,
                                                                                                                    df_with_rankings=methods_in_period_df,
                                                                                                                    numbered_ranking=empirical_ranking_num,
                                                                                                                    chord_label_column=labels_to_compare_with_rank,
                                                                                                                    column_to_compare_with_emp=column_to_compare_with_rank)
            smaller_corr_df = pd.DataFrame({
                'correlation':[correlation],
                'scores_based_on_emp_rank':[scores_for_each_chord_based_on_emp],
                'p_value':[p_value],
                'subharmonic_method':[method],
                'periods_considered':[p_case],
    
            })

            # print(smaller_corr_df)
            # return
            for_all_corr_df = pd.concat([for_all_corr_df,smaller_corr_df], ignore_index=True)

    return for_all_corr_df

            

### We now have corr df per case per period, we need to do per threshold as well

In [14]:
def create_corr_df_for_subharmonic_per_threshold(subharmonic_df, 
                                   empirical_ranking=[],
                                   empirical_ranking_num=None,
                                   labels_to_compare_with_rank='chord_labels', 
                                   column_to_compare_with_rank='normalized_tension_score',
                                   break_into_methods='case',
                                   periods='periods_considered',
                                   threshold_column='threshold_exponent'):
    all_corr_df = pd.DataFrame()

    for threshold in subharmonic_df[threshold_column].unique():
        print(f'Now processing threshold {threshold}')


        threshold_df = subharmonic_df[subharmonic_df[threshold_column]==threshold]

        corr_df_for_threshold = create_corr_df_for_subharmonic_periods_cases(subharmonic_df=threshold_df,
                                                                             empirical_ranking=empirical_ranking,
                                                                             empirical_ranking_num=empirical_ranking_num,
                                                                             labels_to_compare_with_rank=labels_to_compare_with_rank,
                                                                             column_to_compare_with_rank=column_to_compare_with_rank,
                                                                             break_into_methods=break_into_methods,
                                                                             periods=periods)
        corr_df_for_threshold['threshold_exponent'] = threshold

        all_corr_df = pd.concat([all_corr_df,corr_df_for_threshold], ignore_index=True)
    return all_corr_df

In [15]:
interval_corr_df_w_thresh_period_case = create_corr_df_for_subharmonic_per_threshold(grouped_df,empirical_ranking=empirical_ranking_intervals,empirical_ranking_num=None, labels_to_compare_with_rank='chord_label',column_to_compare_with_rank='normalized_tension_score',break_into_methods='case',periods='periods_considered')

Now processing threshold 10**1


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:429: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**10
Now processing threshold 10**11
Now processing threshold 10**12
Now processing threshold 10**2


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:429: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**3


...

Now processing threshold 10**4


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:429: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**5


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:429: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**6
Now processing threshold 10**7
Now processing threshold 10**8
Now processing threshold 10**9


In [16]:
interval_corr_df_w_thresh_period_case

correlation                           scores_based_on_emp_rank  \
0             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
1             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
3             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
...           ...                                                ...   
3127    -0.357453  [0.0, 0.0, 1.0, 0.6546922875876561, 0.02493322...   
3128    -0.378209  [0.0, 0.0, 1.0, 0.6546922875876561, 0.01110522...   
3129    -0.017090  [0.3018200784198099, 0.0, 0.7214823642898025, ...   
3130     0.616830  [0.0, 0.1310116144078594, 0.0869765634637853, ...   
3131     0.611701  [0.0, 0.1310116144078594, 0.0869765634637853, ...   

       p_value                                 subharmonic_method  \
0          NaN          Smallest_delta_t_and_choose_top_3_delta_t   
1          NaN      Smallest_delta_t_and_filter_by_smallest_ratio   
2          NaN  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
3          NaN              Smallest_ratio_and_choose_top_3_ratio   
4          NaN      Smallest_ratio_and_filter_by_smallest_delta_t   
...        ...                                                ...   
3127  0.230495      Smallest_ratio_and_filter_by_smallest_delta_t   
3128  0.202582        Smallest_ratio_and_filter_by_smallest_t_sub   
3129  0.955809              Smallest_t_sub_and_choose_top_3_t_sub   
3130  0.024731      Smallest_t_sub_and_filter_by_smallest_delta_t   
3131  0.026305        Smallest_t_sub_and_filter_by_smallest_ratio   

      periods_considered threshold_exponent  
0                      4              10**1  
1                      4              10**1  
2                      4              10**1  
3                      4              10**1  
4                      4              10**1  
...                  ...                ...  
3127                  32              10**9  
3128                  32              10**9  
3129                  32              10**9  
3130                  32              10**9  
3131                  32              10**9  

[3132 rows x 6 columns]

In [17]:
interval_corr_df_w_thresh_period_case.to_csv('../data_csvs/subharmonic_correlation_intervals_for_thresholds_period_case.csv',index=False)

# Start triad correlation with threshold

In [18]:
subharmonics_df = pipeline_for_threshold_considered(notes_to_consider=triads,chord_labels=chord_labels_triads,threshold_exponents=threshold_exponents,periods_considered=periods_considered)
subharmonics_df.to_csv('../data_csvs/triad_subharmonic_w_threshholds.csv')




Now processing threshold exponent 1
Now processing threshold exponent 2
Now processing threshold exponent 3
Now processing threshold exponent 4
Now processing threshold exponent 5
Now processing threshold exponent 6
Now processing threshold exponent 7
Now processing threshold exponent 8
Now processing threshold exponent 9
Now processing threshold exponent 10
Now processing threshold exponent 11
Now processing threshold exponent 12


6 methods * 13 chords * 12 thresholds  *29 perriods

In [19]:
del subharmonics_df

In [20]:
triad_subharmonic_df = pd.read_csv('../data_csvs/triad_subharmonic_w_threshholds.csv',)
triad_subharmonic_df.drop(['Unnamed: 0'], axis=1, inplace=True)
triad_subharmonic_df

t_values  mean_t_sub  \
0       [0.00382225643297143, 0.003033726941295533, 0....    0.003136   
1       [0.00382225643297143, 0.003033726941295533, 0....    0.003986   
2       [0.00764451286594286, 0.006067453882591066, 0....    0.006271   
3       [0.00382225643297143, 0.003033726941295533, 0....    0.003136   
4       [0.00764451286594286, 0.009101180823886598, 0....    0.008133   
...                                                   ...         ...   
122143  [0.05733384649457145, 0.057640811884615124, 0....    0.057588   
122144  [0.07262287222645716, 0.07280944659109279, 0.0...    0.072556   
122145  [0.05733384649457145, 0.057640811884615124, 0....    0.057588   
122146  [0.07262287222645716, 0.07280944659109279, 0.0...    0.072556   
122147  [0.04586707719565716, 0.04550590411943299, 0.0...    0.045708   

                 indices  difference_(delta_t)  \
0          [0.0, 0, 0.0]              0.001271   
1          [0.0, 0, 1.0]              0.002068   
2          [1.0, 1, 1.0]              0.002542   
3          [0.0, 0, 0.0]              0.001271   
4          [1.0, 2, 2.0]              0.001457   
...                  ...                   ...   
122143  [14.0, 18, 23.0]              0.000455   
122144  [18.0, 23, 29.0]              0.000573   
122145  [14.0, 18, 23.0]              0.000455   
122146  [18.0, 23, 29.0]              0.000573   
122147  [11.0, 14, 18.0]              0.000361   

        difference_ratio_(delta_t_hat)  \
0                             0.405401   
1                             0.518906   
2                             0.405401   
3                             0.405401   
4                             0.179107   
...                                ...   
122143                        0.007902   
122144                        0.007902   
122145                        0.007902   
122146                        0.007902   
122147                        0.007902   

                                                     case  tension_score  \
0       Smallest_delta_t_and_filter_by_smallest_t_sub_...       0.000000   
1       Smallest_delta_t_and_filter_by_smallest_t_sub_...       0.000000   
2       Smallest_delta_t_and_filter_by_smallest_t_sub_...       0.000000   
3               Smallest_delta_t_and_choose_top_3_delta_t       0.000000   
4               Smallest_delta_t_and_choose_top_3_delta_t       0.000000   
...                                                   ...            ...   
122143      Smallest_ratio_and_filter_by_smallest_delta_t  986798.451886   
122144      Smallest_ratio_and_filter_by_smallest_delta_t  986798.451886   
122145              Smallest_ratio_and_choose_top_3_ratio  986798.451886   
122146              Smallest_ratio_and_choose_top_3_ratio  986798.451886   
122147              Smallest_ratio_and_choose_top_3_ratio  986798.451886   

       note_names chord_label  normalized_tension_score  periods_considered  \
0        C4,E4,G4          CM                  0.000000                   4   
1        C4,E4,G4          CM                  0.000000                   4   
2        C4,E4,G4          CM                  0.000000                   4   
3        C4,E4,G4          CM                  0.000000                   4   
4        C4,E4,G4          CM                  0.000000                   4   
...           ...         ...                       ...                 ...   
122143  C4,E4,G#4        CAug                  0.036666                  32   
122144  C4,E4,G#4        CAug                  0.036666                  32   
122145  C4,E4,G#4        CAug                  0.041219                  32   
122146  C4,E4,G#4        CAug                  0.041219                  32   
122147  C4,E4,G#4        CAug                  0.041219                  32   

       threshold_exponent  
0                   10**1  
1                   10**1  
2                   10**1  
3                   10**1  
4                   10**1  
...                   ...  
122143  

In [21]:
triad_subharmonic_df = triad_subharmonic_df.drop(['t_values','mean_t_sub','indices', 'difference_(delta_t)', 'difference_ratio_(delta_t_hat)'], axis=1)
triad_subharmonic_df = triad_subharmonic_df.groupby(['case','note_names','periods_considered','threshold_exponent']).first().reset_index()
triad_subharmonic_df

case note_names  \
0        Smallest_delta_t_and_choose_top_3_delta_t  C4,D#4,A4   
1        Smallest_delta_t_and_choose_top_3_delta_t  C4,D#4,A4   
2        Smallest_delta_t_and_choose_top_3_delta_t  C4,D#4,A4   
3        Smallest_delta_t_and_choose_top_3_delta_t  C4,D#4,A4   
4        Smallest_delta_t_and_choose_top_3_delta_t  C4,D#4,A4   
...                                            ...        ...   
40711  Smallest_t_sub_and_filter_by_smallest_ratio   C4,F4,G4   
40712  Smallest_t_sub_and_filter_by_smallest_ratio   C4,F4,G4   
40713  Smallest_t_sub_and_filter_by_smallest_ratio   C4,F4,G4   
40714  Smallest_t_sub_and_filter_by_smallest_ratio   C4,F4,G4   
40715  Smallest_t_sub_and_filter_by_smallest_ratio   C4,F4,G4   

       periods_considered threshold_exponent  tension_score chord_label  \
0                       4              10**1       0.000000     Adim1st   
1                       4             10**10    8513.101364     Adim1st   
2                       4             10**11    8513.101364     Adim1st   
3                       4             10**12    8513.101364     Adim1st   
4                       4              10**2       0.000000     Adim1st   
...                   ...                ...            ...         ...   
40711                  32              10**5    8827.264915       Csus4   
40712                  32              10**6    8827.264915       Csus4   
40713                  32              10**7    8827.264915       Csus4   
40714                  32              10**8    8827.264915       Csus4   
40715                  32              10**9    8827.264915       Csus4   

       normalized_tension_score  
0                      0.000000  
1                      0.183563  
2                      0.183563  
3                      0.183563  
4                      0.000000  
...                         ...  
40711                  0.416963  
40712                  0.416963  
40713                  0.416963  
40714                  0.416963  
40715                  0.416963  

[40716 rows x 7 columns]

In [22]:
### now after getting this csv correlation
triad_corr_df_w_thresh_period_case = create_corr_df_for_subharmonic_per_threshold(triad_subharmonic_df,empirical_ranking=empirical_ranking_triads,empirical_ranking_num=None, labels_to_compare_with_rank='chord_label',column_to_compare_with_rank='normalized_tension_score',break_into_methods='case',periods='periods_considered')
triad_corr_df_w_thresh_period_case['compared_with']='Ranking Order'

triad_corr_df_emp_rank = create_corr_df_for_subharmonic_per_threshold(triad_subharmonic_df,empirical_ranking=empirical_ranking_triads,empirical_ranking_num=empirical_ranking_nums_triads, labels_to_compare_with_rank='chord_label',column_to_compare_with_rank='normalized_tension_score',break_into_methods='case',periods='periods_considered')
triad_corr_df_emp_rank['compared_with']='Numerical Ranking'

triads_complete = pd.concat([triad_corr_df_w_thresh_period_case,triad_corr_df_emp_rank], ignore_index=True)
triads_complete.to_csv('../data_csvs/subharmonic_correlation_triads_for_thresholds_period_case_both_ranks.csv',index=False)

Now processing threshold 10**1


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:429: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**10
Now processing threshold 10**11
Now processing threshold 10**12
Now processing threshold 10**2


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:429: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**3


...

Now processing threshold 10**4


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:429: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**5


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:429: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**6
Now processing threshold 10**7
Now processing threshold 10**8
Now processing threshold 10**9


6 methods * 12 thresholds * 29 periods * 2 compared with = 4176 rows

In [23]:
triads_complete = pd.read_csv('../data_csvs/subharmonic_correlation_triads_for_thresholds_period_case_both_ranks.csv',)
triads_complete['exp_with']= 'Triads'
for i, r in triads_complete.iterrows():
    if triads_complete.at[i, 'compared_with']=='Ranking Order':
        triads_complete.at[i, 'ground_truth_type']= 'Triads - Ranking Order'
    elif triads_complete.at[i, 'compared_with']=='Numerical Ranking':
        triads_complete.at[i, 'ground_truth_type']= 'Triads - Numerical Ranking'
triads_complete.to_csv('../data_csvs/subharmonic_correlation_triads_for_thresholds_period_case_both_ranks.csv',index=False)

In [24]:
interval_corr_df_w_thresh_period_case = pd.read_csv('../data_csvs/subharmonic_correlation_intervals_for_thresholds_period_case.csv',)

interval_corr_df_w_thresh_period_case['compared_with']='Ranking Order'
interval_corr_df_w_thresh_period_case['exp_with']= 'Intervals'
for i, r in interval_corr_df_w_thresh_period_case.iterrows():
    interval_corr_df_w_thresh_period_case.at[i, 'ground_truth_type']= 'Intervals - Ranking Order'

interval_corr_df_w_thresh_period_case.to_csv('../data_csvs/subharmonic_correlation_intervals_for_thresholds_period_case.csv',index=False)


In [25]:

all_exp = pd.concat([interval_corr_df_w_thresh_period_case,triads_complete], ignore_index=True)
all_exp

correlation                           scores_based_on_emp_rank  \
0             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
1             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
3             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
...           ...                                                ...   
9391    -0.090093  [0.0699652214329859, 0.0432816229688778, 0.104...   
9392    -0.115147  [0.0797299274768871, 0.0533264878855439, 0.114...   
9393    -0.066339  [0.5498627292790443, 0.7613911099998745, 0.147...   
9394    -0.025800  [0.090567557665143, 0.4329291561745582, 0.1540...   
9395     0.214101  [0.0, 0.0610141689862492, 0.368078156640452, 0...   

       p_value                                 subharmonic_method  \
0          NaN          Smallest_delta_t_and_choose_top_3_delta_t   
1          NaN      Smallest_delta_t_and_filter_by_smallest_ratio   
2          NaN  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
3          NaN              Smallest_ratio_and_choose_top_3_ratio   
4          NaN      Smallest_ratio_and_filter_by_smallest_delta_t   
...        ...                                                ...   
9391  0.769752      Smallest_ratio_and_filter_by_smallest_delta_t   
9392  0.707970        Smallest_ratio_and_filter_by_smallest_t_sub   
9393  0.829515              Smallest_t_sub_and_choose_top_3_t_sub   
9394  0.933325      Smallest_t_sub_and_filter_by_smallest_delta_t   
9395  0.482442        Smallest_t_sub_and_filter_by_smallest_ratio   

      periods_considered threshold_exponent      compared_with   exp_with  \
0                      4              10**1      Ranking Order  Intervals   
1                      4              10**1      Ranking Order  Intervals   
2                      4              10**1      Ranking Order  Intervals   
3                      4              10**1      Ranking Order  Intervals   
4                      4              10**1      Ranking Order  Intervals   
...                  ...                ...                ...        ...   
9391                  32              10**9  Numerical Ranking     Triads   
9392                  32              10**9  Numerical Ranking     Triads   
9393                  32              10**9  Numerical Ranking     Triads   
9394                  32              10**9  Numerical Ranking     Triads   
9395                  32              10**9  Numerical Ranking     Triads   

               ground_truth_type  
0      Intervals - Ranking Order  
1      Intervals - Ranking Order  
2      Intervals - Ranking Order  
3      Intervals - Ranking Order  
4      Intervals - Ranking Order  
...                          ...  
9391  Triads - Numerical Ranking  
9392  Triads - Numerical Ranking  
9393  Triads - Numerical Ranking  
9394  Triads - Numerical Ranking  
9395  Triads - Numerical Ranking  

[9396 rows x 9 columns]

## Clean method names abstract

In [26]:


all_exp = clean_subharmonic_method_names(all_exp)
all_exp

correlation                           scores_based_on_emp_rank  \
0             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
1             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
3             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
...           ...                                                ...   
9391    -0.090093  [0.0699652214329859, 0.0432816229688778, 0.104...   
9392    -0.115147  [0.0797299274768871, 0.0533264878855439, 0.114...   
9393    -0.066339  [0.5498627292790443, 0.7613911099998745, 0.147...   
9394    -0.025800  [0.090567557665143, 0.4329291561745582, 0.1540...   
9395     0.214101  [0.0, 0.0610141689862492, 0.368078156640452, 0...   

       p_value                                 subharmonic_method  \
0          NaN          Smallest_delta_t_and_choose_top_3_delta_t   
1          NaN      Smallest_delta_t_and_filter_by_smallest_ratio   
2          NaN  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
3          NaN              Smallest_ratio_and_choose_top_3_ratio   
4          NaN      Smallest_ratio_and_filter_by_smallest_delta_t   
...        ...                                                ...   
9391  0.769752      Smallest_ratio_and_filter_by_smallest_delta_t   
9392  0.707970        Smallest_ratio_and_filter_by_smallest_t_sub   
9393  0.829515              Smallest_t_sub_and_choose_top_3_t_sub   
9394  0.933325      Smallest_t_sub_and_filter_by_smallest_delta_t   
9395  0.482442        Smallest_t_sub_and_filter_by_smallest_ratio   

      periods_considered threshold_exponent      compared_with   exp_with  \
0                      4              10**1      Ranking Order  Intervals   
1                      4              10**1      Ranking Order  Intervals   
2                      4              10**1      Ranking Order  Intervals   
3                      4              10**1      Ranking Order  Intervals   
4                      4              10**1      Ranking Order  Intervals   
...                  ...                ...                ...        ...   
9391                  32              10**9  Numerical Ranking     Triads   
9392                  32              10**9  Numerical Ranking     Triads   
9393                  32              10**9  Numerical Ranking     Triads   
9394                  32              10**9  Numerical Ranking     Triads   
9395                  32              10**9  Numerical Ranking     Triads   

               ground_truth_type clean_subharmonic_method  
0      Intervals - Ranking Order                 Method B  
1      Intervals - Ranking Order                 Method C  
2      Intervals - Ranking Order                 Method A  
3      Intervals - Ranking Order                 Method I  
4      Intervals - Ranking Order                 Method H  
...                          ...                      ...  
9391  Triads - Numerical Ranking                 Method H  
9392  Triads - Numerical Ranking                 Method G  
9393  Triads - Numerical Ranking                 Method D  
9394  Triads - Numerical Ranking                 Method E  
9395  Triads - Numerical Ranking                 Method F  

[9396 rows x 10 columns]

In [27]:
all_exp.subharmonic_method.unique()


array(['Smallest_delta_t_and_choose_top_3_delta_t',
       'Smallest_delta_t_and_filter_by_smallest_ratio',
       "Smallest_delta_t_and_filter_by_smallest_t_sub_(Chan's_method?)",
       'Smallest_ratio_and_choose_top_3_ratio',
       'Smallest_ratio_and_filter_by_smallest_delta_t',
       'Smallest_ratio_and_filter_by_smallest_t_sub',
       'Smallest_t_sub_and_choose_top_3_t_sub',
       'Smallest_t_sub_and_filter_by_smallest_delta_t',
       'Smallest_t_sub_and_filter_by_smallest_ratio'], dtype=object)

In [28]:
all_exp.to_csv('../data_csvs/all_subharmonic_correlation_intervals_and_triads_for_thresholds_period_case_both_ranks.csv',index=False)

# Finished csv, read csv with complete subharmonics


In [14]:
import altair as alt
import pandas as pd

In [15]:
all_exp = pd.read_csv('../data_csvs/all_subharmonic_correlation_intervals_and_triads_for_thresholds_period_case_both_ranks.csv')
all_exp


correlation                           scores_based_on_emp_rank  \
0             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
1             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
3             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
...           ...                                                ...   
9391    -0.090093  [0.0699652214329859, 0.0432816229688778, 0.104...   
9392    -0.115147  [0.0797299274768871, 0.0533264878855439, 0.114...   
9393    -0.066339  [0.5498627292790443, 0.7613911099998745, 0.147...   
9394    -0.025800  [0.090567557665143, 0.4329291561745582, 0.1540...   
9395     0.214101  [0.0, 0.0610141689862492, 0.368078156640452, 0...   

       p_value                                 subharmonic_method  \
0          NaN          Smallest_delta_t_and_choose_top_3_delta_t   
1          NaN      Smallest_delta_t_and_filter_by_smallest_ratio   
2          NaN  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
3          NaN              Smallest_ratio_and_choose_top_3_ratio   
4          NaN      Smallest_ratio_and_filter_by_smallest_delta_t   
...        ...                                                ...   
9391  0.769752      Smallest_ratio_and_filter_by_smallest_delta_t   
9392  0.707970        Smallest_ratio_and_filter_by_smallest_t_sub   
9393  0.829515              Smallest_t_sub_and_choose_top_3_t_sub   
9394  0.933325      Smallest_t_sub_and_filter_by_smallest_delta_t   
9395  0.482442        Smallest_t_sub_and_filter_by_smallest_ratio   

      periods_considered threshold_exponent      compared_with   exp_with  \
0                      4              10**1      Ranking Order  Intervals   
1                      4              10**1      Ranking Order  Intervals   
2                      4              10**1      Ranking Order  Intervals   
3                      4              10**1      Ranking Order  Intervals   
4                      4              10**1      Ranking Order  Intervals   
...                  ...                ...                ...        ...   
9391                  32              10**9  Numerical Ranking     Triads   
9392                  32              10**9  Numerical Ranking     Triads   
9393                  32              10**9  Numerical Ranking     Triads   
9394                  32              10**9  Numerical Ranking     Triads   
9395                  32              10**9  Numerical Ranking     Triads   

               ground_truth_type clean_subharmonic_method  \
0      Intervals - Ranking Order                 Method B   
1      Intervals - Ranking Order                 Method C   
2      Intervals - Ranking Order                 Method A   
3      Intervals - Ranking Order                 Method I   
4      Intervals - Ranking Order                 Method H   
...                          ...                      ...   
9391  Triads - Numerical Ranking                 Method H   
9392  Triads - Numerical Ranking                 Method G   
9393  Triads - Numerical Ranking                 Method D   
9394  Triads - Numerical Ranking                 Method E   
9395  Triads - Numerical Ranking                 Method F   

               method_focus  
0           Delta_t focused  
1           Delta_t focused  
2           Delta_t focused  
3     Delta_t/T_sub focused  
4     Delta_t/T_sub focused  
...                     ...  
9391  Delta_t/T_sub focused  
9392  Delta_t/T_sub focused  
9393          T_sub focused  
9394          T_sub focused  
9395          T_sub focused  

[9396 rows x 11 columns]

In [16]:
all_exp = add_method_focus_column(all_exp)
all_exp.to_csv('../data_csvs/all_subharmonic_correlation_intervals_and_triads_for_thresholds_period_case_both_ranks.csv',index=False)

In [17]:
all_exp = clean_subharmonic_method_names(all_exp)
all_exp = add_method_focus_column(all_exp)
all_exp.to_csv('../data_csvs/all_subharmonic_correlation_intervals_and_triads_for_thresholds_period_case_both_ranks.csv',index=False)
all_exp

correlation                           scores_based_on_emp_rank  \
0             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
1             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
3             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
...           ...                                                ...   
9391    -0.090093  [0.0699652214329859, 0.0432816229688778, 0.104...   
9392    -0.115147  [0.0797299274768871, 0.0533264878855439, 0.114...   
9393    -0.066339  [0.5498627292790443, 0.7613911099998745, 0.147...   
9394    -0.025800  [0.090567557665143, 0.4329291561745582, 0.1540...   
9395     0.214101  [0.0, 0.0610141689862492, 0.368078156640452, 0...   

       p_value                                 subharmonic_method  \
0          NaN          Smallest_delta_t_and_choose_top_3_delta_t   
1          NaN      Smallest_delta_t_and_filter_by_smallest_ratio   
2          NaN  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
3          NaN              Smallest_ratio_and_choose_top_3_ratio   
4          NaN      Smallest_ratio_and_filter_by_smallest_delta_t   
...        ...                                                ...   
9391  0.769752      Smallest_ratio_and_filter_by_smallest_delta_t   
9392  0.707970        Smallest_ratio_and_filter_by_smallest_t_sub   
9393  0.829515              Smallest_t_sub_and_choose_top_3_t_sub   
9394  0.933325      Smallest_t_sub_and_filter_by_smallest_delta_t   
9395  0.482442        Smallest_t_sub_and_filter_by_smallest_ratio   

      periods_considered threshold_exponent      compared_with   exp_with  \
0                      4              10**1      Ranking Order  Intervals   
1                      4              10**1      Ranking Order  Intervals   
2                      4              10**1      Ranking Order  Intervals   
3                      4              10**1      Ranking Order  Intervals   
4                      4              10**1      Ranking Order  Intervals   
...                  ...                ...                ...        ...   
9391                  32              10**9  Numerical Ranking     Triads   
9392                  32              10**9  Numerical Ranking     Triads   
9393                  32              10**9  Numerical Ranking     Triads   
9394                  32              10**9  Numerical Ranking     Triads   
9395                  32              10**9  Numerical Ranking     Triads   

               ground_truth_type clean_subharmonic_method  \
0      Intervals - Ranking Order                 Method B   
1      Intervals - Ranking Order                 Method C   
2      Intervals - Ranking Order                 Method A   
3      Intervals - Ranking Order                 Method I   
4      Intervals - Ranking Order                 Method H   
...                          ...                      ...   
9391  Triads - Numerical Ranking                 Method H   
9392  Triads - Numerical Ranking                 Method G   
9393  Triads - Numerical Ranking                 Method D   
9394  Triads - Numerical Ranking                 Method E   
9395  Triads - Numerical Ranking                 Method F   

               method_focus  
0           Delta_t focused  
1           Delta_t focused  
2           Delta_t focused  
3     Delta_t/T_sub focused  
4     Delta_t/T_sub focused  
...                     ...  
9391  Delta_t/T_sub focused  
9392  Delta_t/T_sub focused  
9393          T_sub focused  
9394          T_sub focused  
9395          T_sub focused  

[9396 rows x 11 columns]

## now that everythings is in order, three things remain
1. threshold average to choose threshold. (boxplot and linechart)
2. boxplot correlation
3. corr line chart
4. case by case
5. correlation grid


### Thresholds

In [18]:
sorted_thresholds = ["10**-" + str(i) for i in range(1,10)]


all_exp['threshold_exponent'] = all_exp['threshold_exponent'].apply(lambda x: "10**" + str(-int(x.split('**')[1])) if '**' in x else x)

all_exp

correlation                           scores_based_on_emp_rank  \
0             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
1             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
3             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
...           ...                                                ...   
9391    -0.090093  [0.0699652214329859, 0.0432816229688778, 0.104...   
9392    -0.115147  [0.0797299274768871, 0.0533264878855439, 0.114...   
9393    -0.066339  [0.5498627292790443, 0.7613911099998745, 0.147...   
9394    -0.025800  [0.090567557665143, 0.4329291561745582, 0.1540...   
9395     0.214101  [0.0, 0.0610141689862492, 0.368078156640452, 0...   

       p_value                                 subharmonic_method  \
0          NaN          Smallest_delta_t_and_choose_top_3_delta_t   
1          NaN      Smallest_delta_t_and_filter_by_smallest_ratio   
2          NaN  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
3          NaN              Smallest_ratio_and_choose_top_3_ratio   
4          NaN      Smallest_ratio_and_filter_by_smallest_delta_t   
...        ...                                                ...   
9391  0.769752      Smallest_ratio_and_filter_by_smallest_delta_t   
9392  0.707970        Smallest_ratio_and_filter_by_smallest_t_sub   
9393  0.829515              Smallest_t_sub_and_choose_top_3_t_sub   
9394  0.933325      Smallest_t_sub_and_filter_by_smallest_delta_t   
9395  0.482442        Smallest_t_sub_and_filter_by_smallest_ratio   

      periods_considered threshold_exponent      compared_with   exp_with  \
0                      4             10**-1      Ranking Order  Intervals   
1                      4             10**-1      Ranking Order  Intervals   
2                      4             10**-1      Ranking Order  Intervals   
3                      4             10**-1      Ranking Order  Intervals   
4                      4             10**-1      Ranking Order  Intervals   
...                  ...                ...                ...        ...   
9391                  32             10**-9  Numerical Ranking     Triads   
9392                  32             10**-9  Numerical Ranking     Triads   
9393                  32             10**-9  Numerical Ranking     Triads   
9394                  32             10**-9  Numerical Ranking     Triads   
9395                  32             10**-9  Numerical Ranking     Triads   

               ground_truth_type clean_subharmonic_method  \
0      Intervals - Ranking Order                 Method B   
1      Intervals - Ranking Order                 Method C   
2      Intervals - Ranking Order                 Method A   
3      Intervals - Ranking Order                 Method I   
4      Intervals - Ranking Order                 Method H   
...                          ...                      ...   
9391  Triads - Numerical Ranking                 Method H   
9392  Triads - Numerical Ranking                 Method G   
9393  Triads - Numerical Ranking                 Method D   
9394  Triads - Numerical Ranking                 Method E   
9395  Triads - Numerical Ranking                 Method F   

               method_focus  
0           Delta_t focused  
1           Delta_t focused  
2           Delta_t focused  
3     Delta_t/T_sub focused  
4     Delta_t/T_sub focused  
...                     ...  
9391  Delta_t/T_sub focused  
9392  Delta_t/T_sub focused  
9393          T_sub focused  
9394          T_sub focused  
9395          T_sub focused  

[9396 rows x 11 columns]

In [19]:


mean_threshold_corr = all_exp.groupby(['threshold_exponent','ground_truth_type','clean_subharmonic_method','method_focus']).agg({'correlation':'mean'}).reset_index()
mean_threshold_corr = mean_threshold_corr[mean_threshold_corr['threshold_exponent'].isin(sorted_thresholds)]

all_exp_filtered = all_exp.dropna()
all_exp_filtered = all_exp_filtered[all_exp_filtered['threshold_exponent'].isin(sorted_thresholds)]
all_exp_filtered


correlation                           scores_based_on_emp_rank  \
1305 -6.938894e-18  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, ...   
1307 -3.711253e-02  [0.0, 0.4344855926108322, 0.4206408396849561, ...   
1309 -6.938894e-18  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, ...   
1310 -1.827459e-01  [0.0, 0.4399280466907606, 0.4259098716000797, ...   
1311 -1.709017e-02  [0.3018200784198099, 0.0, 0.7214823642898025, ...   
...            ...                                                ...   
9391 -9.009299e-02  [0.0699652214329859, 0.0432816229688778, 0.104...   
9392 -1.151466e-01  [0.0797299274768871, 0.0533264878855439, 0.114...   
9393 -6.633915e-02  [0.5498627292790443, 0.7613911099998745, 0.147...   
9394 -2.579985e-02  [0.090567557665143, 0.4329291561745582, 0.1540...   
9395  2.141005e-01  [0.0, 0.0610141689862492, 0.368078156640452, 0...   

       p_value                                 subharmonic_method  \
1305  1.000000          Smallest_delta_t_and_choose_top_3_delta_t   
1307  0.904192  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
1309  1.000000      Smallest_ratio_and_filter_by_smallest_delta_t   
1310  0.550122        Smallest_ratio_and_filter_by_smallest_t_sub   
1311  0.955809              Smallest_t_sub_and_choose_top_3_t_sub   
...        ...                                                ...   
9391  0.769752      Smallest_ratio_and_filter_by_smallest_delta_t   
9392  0.707970        Smallest_ratio_and_filter_by_smallest_t_sub   
9393  0.829515              Smallest_t_sub_and_choose_top_3_t_sub   
9394  0.933325      Smallest_t_sub_and_filter_by_smallest_delta_t   
9395  0.482442        Smallest_t_sub_and_filter_by_smallest_ratio   

      periods_considered threshold_exponent      compared_with   exp_with  \
1305                   4             10**-3      Ranking Order  Intervals   
1307                   4             10**-3      Ranking Order  Intervals   
1309                   4             10**-3      Ranking Order  Intervals   
1310                   4             10**-3      Ranking Order  Intervals   
1311                   4             10**-3      Ranking Order  Intervals   
...                  ...                ...                ...        ...   
9391                  32             10**-9  Numerical Ranking     Triads   
9392                  32             10**-9  Numerical Ranking     Triads   
9393                  32             10**-9  Numerical Ranking     Triads   
9394                  32             10**-9  Numerical Ranking     Triads   
9395                  32             10**-9  Numerical Ranking     Triads   

               ground_truth_type clean_subharmonic_method  \
1305   Intervals - Ranking Order                 Method B   
1307   Intervals - Ranking Order                 Method A   
1309   Intervals - Ranking Order                 Method H   
1310   Intervals - Ranking Order                 Method G   
1311   Intervals - Ranking Order                 Method D   
...                          ...                      ...   
9391  Triads - Numerical Ranking                 Method H   
9392  Triads - Numerical Ranking                 Method G   
9393  Triads - Numerical Ranking                 Method D   
9394  Triads - Numerical Ranking                 Method E   
9395  Triads - Numerical Ranking                 Method F   

               method_focus  
1305        Delta_t focused  
1307        Delta_t focused  
1309  Delta_t/T_sub focused  
1310  Delta_t/T_sub focused  
1311          T_sub focused  
...                     ...  
9391  Delta_t/T_sub focused  
9392  Delta_t/T_sub focused  
9393          T_sub focused  
9394          T_sub focused  
9395          T_sub focused  

[4538 rows x 11 columns]

In [20]:
alt.Chart(all_exp_filtered).mark_boxplot().encode(
    x=alt.X('threshold_exponent', sort=sorted_thresholds, title='Threshold Exponent'),
    y=alt.Y('correlation', title='Correlation Coefficient'),

    # color=alt.Color('method_focus:N', title='Method Focus'),
    # column=alt.Column('ground_truth_type:N', title='Ground Truth Type')
).properties(
    height=200
).facet(
    column=alt.Column('ground_truth_type:N', title='Ground Truth Type')
).properties(
    title='Subharmonic Tension Model Correlation using Different Thresholds for Chan\'s Equation'
).configure_title(
    anchor='middle'
)

alt.FacetChart(...)

In [21]:
alt.Chart(mean_threshold_corr.dropna()).mark_line().encode(
    x=alt.X('threshold_exponent', sort=sorted_thresholds, title='Threshold Exponent', axis=alt.Axis(grid=True,),scale=alt.Scale(zero=False)),
    y=alt.Y('correlation', title='Correlation Coefficient ',axis=alt.Axis(grid=True)),
    color=alt.Color('ground_truth_type:N', title='Ground Truth Type',),
    facet=alt.Facet('clean_subharmonic_method:N',
                     title='Subharmonic Methods',
                     columns=3,
                     spacing={'column': 0.2, 'row': 0.2},
                     ),
).properties(height=150,width=150
             ,title="Correlation Average Using Different Thresholds on Method").configure_legend(
    orient='bottom',
    
    ).configure_title(
        anchor='middle'
    )
# ).properties(
#     title='Mean Subharmonic Tension Model Correlation with Empirical Rankings for Intervals and Triads'
# )


alt.Chart(...)

### Correlation linecharts

In [22]:
## Choosing 10**5 as threshold exponent
t_exp ="10**-7"
all_exp_threshold_10_5 = all_exp_filtered[all_exp_filtered['threshold_exponent']==t_exp]

In [23]:
alt.Chart(all_exp_threshold_10_5).mark_boxplot().encode(
    x=alt.X('clean_subharmonic_method:N', title='Subharmonic Method',axis=alt.Axis(labelAngle=-45)),
    y=alt.Y('correlation', title='Correlation Coefficient', axis=alt.Axis(grid=True, tickCount=10) ,scale=alt.Scale(domain=[-0.80,1])),
    color=alt.Color('method_focus:N', title='Method Focus'),
    facet=alt.Facet('ground_truth_type:N', title='Ground Truth Type',columns=3,spacing={'column': 0.2, 'row': 0.2})
).properties(
    width=200,
    height=175,
    title=f'Distribution of Correlation Coefficients for {t_exp} Threshold Exponent'
).configure_legend(
    orient='bottom'
).configure_title(
    anchor='middle'
)


alt.Chart(...)

In [24]:
## Correlation line charts
alt.Chart(all_exp_threshold_10_5).mark_line(opacity=0.7).encode(
    x=alt.X('periods_considered', title='Period-Cycles Considered',
                axis=alt.Axis(labelAngle=-45,grid=True)),
    y=alt.Y('correlation', title='Correlation Coefficient',axis=alt.Axis(grid=True)),
    color=alt.Color('clean_subharmonic_method:N', title='Subharmonic Method'),
    shape=alt.Shape('method_focus', title="Method Focus"),
    ).properties(
        width=250,
        height=250,
        
    ).facet(
    column=alt.Column('ground_truth_type:N', title='Ground truths considered')
    ).properties(
        title=f'Correlation Coefficient Varying as Cycles Considered Increase for Different Methods using {t_exp} Threshold Exponent'
    ).configure_title(
        anchor='middle'
    ).configure_legend(
        orient='bottom',
        titleAnchor='start',
        direction='vertical',
        labelAlign='left',
        columns=3
    ).resolve_scale(shape='shared')

alt.FacetChart(...)

## Corr heatmap



In [25]:
# color = alt.datum.correlation > 0.5 

df_harm = all_exp_threshold_10_5[all_exp_threshold_10_5['periods_considered']<=24]

corr_cart = alt.Chart(df_harm).mark_rect(align='center',stroke='black',strokeWidth=0.5).encode(
    x=alt.X('periods_considered:O',scale=alt.Scale(clamp=True),axis=alt.Axis(title='Periods Considered',labelAngle=0)),
    y=alt.Y('clean_subharmonic_method:O'),
    color=alt.Color('correlation:Q', title="Correlation Coefficient",scale=alt.Scale(domain=[-0.6, 1], scheme='viridis'),
                    ),
)

predicate = alt.datum.correlation >= 0.25
text_chart = alt.Chart(df_harm).mark_text( align='center').encode(
    x=alt.X('periods_considered:O',scale=alt.Scale(clamp=True)),
    y=alt.Y('clean_subharmonic_method:O', title=None),
    text=alt.Text('correlation:Q',format='.3f'),
    color=alt.condition(predicate, alt.value('black'), alt.value('white'))
)
(corr_cart + text_chart).properties(width=800, height=225).facet(
    row=alt.Row('ground_truth_type:N', title="Correlation Between Different Methods on Different Ground Truths")
    ).properties(
        title=f"Heatmap of Correlation with Varying Periods using {t_exp} Threshold Exponent"
    ).configure_title(
        anchor='middle'
    ).configure_legend(
        # orient='bottom',
        titleOrient='right',
        
    )


alt.FacetChart(...)

## Case by Case

In [26]:
from psychoacoustic_tension_chan_module import interharmonic_module as ihm

In [27]:
intervals = all_exp_threshold_10_5[all_exp_threshold_10_5['exp_with']=='Intervals']
triads_ranking = all_exp_threshold_10_5[(all_exp_threshold_10_5['exp_with']=='Triads') & (all_exp_threshold_10_5['compared_with']=='Ranking Order')]

triads_emp = all_exp_threshold_10_5[(all_exp_threshold_10_5['exp_with']=='Triads') & (all_exp_threshold_10_5['compared_with']=='Numerical Ranking')]
intervals

correlation                           scores_based_on_emp_rank  \
2349     0.603380  [0.0, 0.1310116144078594, 0.1146751176212621, ...   
2350     0.585925  [0.0, 0.1310116144078594, 0.1441768819221, 0.1...   
2351     0.563821  [0.0, 0.0416226800764534, 0.0402963858757446, ...   
2352     0.585925  [0.0, 0.1310116144078594, 0.1441768819221, 0.1...   
2353     0.603380  [0.0, 0.1310116144078594, 0.1146751176212621, ...   
...           ...                                                ...   
2605     0.737505  [0.0, 0.0, 0.0, 0.0, 0.3523816216618904, 0.451...   
2606     0.799915  [0.0, 0.0, 0.0, 0.0, 0.3399992683140064, 0.225...   
2607    -0.017090  [0.3018200784198099, 0.0, 0.7214823642898025, ...   
2608     0.616830  [0.0, 0.1310116144078594, 0.0869765634637853, ...   
2609     0.611701  [0.0, 0.1310116144078594, 0.0869765634637853, ...   

       p_value                                 subharmonic_method  \
2349  0.029014          Smallest_delta_t_and_choose_top_3_delta_t   
2350  0.035355      Smallest_delta_t_and_filter_by_smallest_ratio   
2351  0.044762  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
2352  0.035355              Smallest_ratio_and_choose_top_3_ratio   
2353  0.029014      Smallest_ratio_and_filter_by_smallest_delta_t   
...        ...                                                ...   
2605  0.004013      Smallest_ratio_and_filter_by_smallest_delta_t   
2606  0.001027        Smallest_ratio_and_filter_by_smallest_t_sub   
2607  0.955809              Smallest_t_sub_and_choose_top_3_t_sub   
2608  0.024731      Smallest_t_sub_and_filter_by_smallest_delta_t   
2609  0.026305        Smallest_t_sub_and_filter_by_smallest_ratio   

      periods_considered threshold_exponent  compared_with   exp_with  \
2349                   4             10**-7  Ranking Order  Intervals   
2350                   4             10**-7  Ranking Order  Intervals   
2351                   4             10**-7  Ranking Order  Intervals   
2352                   4             10**-7  Ranking Order  Intervals   
2353                   4             10**-7  Ranking Order  Intervals   
...                  ...                ...            ...        ...   
2605                  32             10**-7  Ranking Order  Intervals   
2606                  32             10**-7  Ranking Order  Intervals   
2607                  32             10**-7  Ranking Order  Intervals   
2608                  32             10**-7  Ranking Order  Intervals   
2609                  32             10**-7  Ranking Order  Intervals   

              ground_truth_type clean_subharmonic_method  \
2349  Intervals - Ranking Order                 Method B   
2350  Intervals - Ranking Order                 Method C   
2351  Intervals - Ranking Order                 Method A   
2352  Intervals - Ranking Order                 Method I   
2353  Intervals - Ranking Order                 Method H   
...                         ...                      ...   
2605  Intervals - Ranking Order                 Method H   
2606  Intervals - Ranking Order                 Method G   
2607  Intervals - Ranking Order                 Method D   
2608  Intervals - Ranking Order                 Method E   
2609  Intervals - Ranking Order                 Method F   

               method_focus  
2349        Delta_t focused  
2350        Delta_t focused  
2351        Delta_t focused  
2352  Delta_t/T_sub focused  
2353  Delta_t/T_sub focused  
...                     ...  
2605  Delta_t/T_sub focused  
2606  Delta_t/T_sub focused  
2607          T_sub focused  
2608          T_sub focused  
2609          T_sub focused  

[261 rows x 11 columns]

In [28]:

intervals_case_case = ihm.convert_correlation_df_to_a_line_chart_df(intervals,empirical_ranking_names=empirical_ranking_intervals,column_to_convert='scores_based_on_emp_rank',group_by_methods_array=['subharmonic_method','clean_subharmonic_method','periods_considered','ground_truth_type','method_focus'])
intervals_case_case

Normalized values for each rank: [0.0, 0.1310116144078594, 0.1146751176212621, 0.1951156775689312, 0.1586199511758766, 0.1597428239254548, 0.0852191017657928, 0.1580093145386703, 0.1672479435253611, 0.2023952518623577, 0.2577716487800783, 0.1823876467906527, 1.0]
Normalized values for each rank: [0.0, 0.1310116144078594, 0.1441768819221, 0.1951156775689312, 0.1586199511758766, 0.1597428239254548, 0.1295417215107807, 0.1580093145386703, 0.1672479435253611, 0.2023952518623577, 0.2180682220232158, 0.1823876467906527, 1.0]
Normalized values for each rank: [0.0, 0.0416226800764534, 0.0402963858757446, 0.0480199262849783, 0.0482708118283227, 0.0756629165776493, 0.0852191017657928, 0.0957976070652699, 0.0449767556231907, 0.0631104243994045, 0.2577716487800783, 0.0512984828918085, 1.0]
Normalized values for each rank: [0.0, 0.1310116144078594, 0.1441768819221, 0.1951156775689312, 0.1586199511758766, 0.1597428239254548, 0.1295417215107807, 0.1580093145386703, 0.1672479435253611, 0.2023952518623

chord_label  normalized_value  \
0              U          0.000000   
1             8v          0.131012   
2             P5          0.114675   
3             P4          0.195116   
4             M3          0.158620   
...          ...               ...   
3388          TT          0.063484   
3389          m7          0.202395   
3390          M2          0.257772   
3391          M7          0.182388   
3392          m2          1.000000   

                               subharmonic_method clean_subharmonic_method  \
0       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
1       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
2       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
3       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
4       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
...                                           ...                      ...   
3388  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   
3389  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   
3390  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   
3391  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   
3392  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   

      periods_considered          ground_truth_type     method_focus  
0                      4  Intervals - Ranking Order  Delta_t focused  
1                      4  Intervals - Ranking Order  Delta_t focused  
2                      4  Intervals - Ranking Order  Delta_t focused  
3                      4  Intervals - Ranking Order  Delta_t focused  
4                      4  Intervals - Ranking Order  Delta_t focused  
...                  ...                        ...              ...  
3388                  32  Intervals - Ranking Order    T_sub focused  
3389                  32  Intervals - Ranking Order    T_sub focused  
3390                  32  Intervals - Ranking Order    T_sub focused  
3391                  32  Intervals - Ranking Order    T_sub focused  
3392                  32  Intervals - Ranking Order    T_sub focused  

[3393 rows x 7 columns]

In [29]:
triads_ranking_case_case = ihm.convert_correlation_df_to_a_line_chart_df(triads_ranking,empirical_ranking_names=empirical_ranking_triads,column_to_convert='scores_based_on_emp_rank',group_by_methods_array=['subharmonic_method','clean_subharmonic_method','periods_considered','ground_truth_type','method_focus'])
triads_ranking_case_case

Normalized values for each rank: [0.4360836390113848, 0.5215672664959862, 0.0054168512343302, 0.0865582199744762, 0.1542894115641612, 1.0, 0.916177907926823, 0.3429978701000641, 0.1835630551170576, 0.0792408169422637, 0.2798141017514379, 0.4625279294380351, 0.0]
Normalized values for each rank: [0.3463827810380342, 0.44546408941737, 0.231947623116921, 0.0, 0.4839381084101148, 1.0, 0.4664005375924641, 0.4470324906437086, 0.1900084084464204, 0.2392315862432824, 0.4333033663094833, 0.377033502956774, 0.0790138217594511]
Normalized values for each rank: [0.0, 0.1109198724250039, 0.4132178027279304, 0.3359505851343858, 0.9271623545075448, 0.2360400456523284, 0.1539602625028244, 0.707350328093148, 1.0, 0.6135942229486009, 0.7999956848164618, 0.1552382297217608, 0.5432648925314469]
Normalized values for each rank: [0.3463827810380342, 0.44546408941737, 0.231947623116921, 0.0, 0.4839381084101148, 1.0, 0.4664005375924641, 0.4470324906437086, 0.1900084084464204, 0.2392315862432824, 0.43330336630

chord_label  normalized_value  \
0             CM          0.436084   
1             Cm          0.521567   
2          FM2nd          0.005417   
3       Fsus42nd          0.086558   
4         G#M1st          0.154289   
...          ...               ...   
3388     Adim1st          0.785346   
3389       Am1st          0.647702   
3390    F#dim2nd          1.000000   
3391        Cdim          0.227790   
3392        CAug          0.152069   

                               subharmonic_method clean_subharmonic_method  \
0       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
1       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
2       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
3       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
4       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
...                                           ...                      ...   
3388  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   
3389  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   
3390  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   
3391  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   
3392  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   

      periods_considered       ground_truth_type     method_focus  
0                      4  Triads - Ranking Order  Delta_t focused  
1                      4  Triads - Ranking Order  Delta_t focused  
2                      4  Triads - Ranking Order  Delta_t focused  
3                      4  Triads - Ranking Order  Delta_t focused  
4                      4  Triads - Ranking Order  Delta_t focused  
...                  ...                     ...              ...  
3388                  32  Triads - Ranking Order    T_sub focused  
3389                  32  Triads - Ranking Order    T_sub focused  
3390                  32  Triads - Ranking Order    T_sub focused  
3391                  32  Triads - Ranking Order    T_sub focused  
3392                  32  Triads - Ranking Order    T_sub focused  

[3393 rows x 7 columns]

In [30]:
triads_ranking_emp_case_case = ihm.convert_correlation_df_to_a_line_chart_df(triads_emp,empirical_ranking_names=empirical_ranking_triads,column_to_convert='scores_based_on_emp_rank',group_by_methods_array=['subharmonic_method','clean_subharmonic_method','periods_considered','ground_truth_type','method_focus'])
triads_ranking_emp_case_case

Normalized values for each rank: [0.4360836390113848, 0.5215672664959862, 0.0054168512343302, 0.0865582199744762, 0.1542894115641612, 1.0, 0.916177907926823, 0.3429978701000641, 0.1835630551170576, 0.0792408169422637, 0.2798141017514379, 0.4625279294380351, 0.0]
Normalized values for each rank: [0.3463827810380342, 0.44546408941737, 0.231947623116921, 0.0, 0.4839381084101148, 1.0, 0.4664005375924641, 0.4470324906437086, 0.1900084084464204, 0.2392315862432824, 0.4333033663094833, 0.377033502956774, 0.0790138217594511]
Normalized values for each rank: [0.0, 0.1109198724250039, 0.4132178027279304, 0.3359505851343858, 0.9271623545075448, 0.2360400456523284, 0.1539602625028244, 0.707350328093148, 1.0, 0.6135942229486009, 0.7999956848164618, 0.1552382297217608, 0.5432648925314469]
Normalized values for each rank: [0.3463827810380342, 0.44546408941737, 0.231947623116921, 0.0, 0.4839381084101148, 1.0, 0.4664005375924641, 0.4470324906437086, 0.1900084084464204, 0.2392315862432824, 0.43330336630

chord_label  normalized_value  \
0             CM          0.436084   
1             Cm          0.521567   
2          FM2nd          0.005417   
3       Fsus42nd          0.086558   
4         G#M1st          0.154289   
...          ...               ...   
3388     Adim1st          0.785346   
3389       Am1st          0.647702   
3390    F#dim2nd          1.000000   
3391        Cdim          0.227790   
3392        CAug          0.152069   

                               subharmonic_method clean_subharmonic_method  \
0       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
1       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
2       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
3       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
4       Smallest_delta_t_and_choose_top_3_delta_t                 Method B   
...                                           ...                      ...   
3388  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   
3389  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   
3390  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   
3391  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   
3392  Smallest_t_sub_and_filter_by_smallest_ratio                 Method F   

      periods_considered           ground_truth_type     method_focus  
0                      4  Triads - Numerical Ranking  Delta_t focused  
1                      4  Triads - Numerical Ranking  Delta_t focused  
2                      4  Triads - Numerical Ranking  Delta_t focused  
3                      4  Triads - Numerical Ranking  Delta_t focused  
4                      4  Triads - Numerical Ranking  Delta_t focused  
...                  ...                         ...              ...  
3388                  32  Triads - Numerical Ranking    T_sub focused  
3389                  32  Triads - Numerical Ranking    T_sub focused  
3390                  32  Triads - Numerical Ranking    T_sub focused  
3391                  32  Triads - Numerical Ranking    T_sub focused  
3392                  32  Triads - Numerical Ranking    T_sub focused  

[3393 rows x 7 columns]

In [31]:
joined_case_by_case = pd.concat([intervals_case_case,triads_ranking_case_case,triads_ranking_emp_case_case], ignore_index=True)
joined_case_by_case.to_csv('../data_csvs/subharmonic_case_by_case_scores_for_intervals_and_triads_threshold_10_5.csv',index=False)

In [32]:
## ground truth for black line
normed_ranking = [1,2,3,4,5,6,7,8,9,10,11,12,13]
normalized_values = [(x - min(normed_ranking)) / (max(normed_ranking) - min(normed_ranking)) for x in normed_ranking]
norm_emp_rankings= [(x - min(empirical_ranking_nums_triads)) / (max(empirical_ranking_nums_triads) - min(empirical_ranking_nums_triads)) for x in empirical_ranking_nums_triads]
norm_emp_rankings

[0.0,
 0.2060133630289532,
 0.29899777282850776,
 0.3298997772828507,
 0.34020044543429834,
 0.4020044543429844,
 0.412305122494432,
 0.5050111358574609,
 0.5155902004454342,
 0.5361915367483295,
 0.5567928730512248,
 0.6185968819599107,
 1.0]

In [33]:
## now plot case case

df_gt_triads = pd.DataFrame({
    'normalized_value':norm_emp_rankings,
    'chord_label':empirical_ranking_triads
})
df_gt_triads_ranking_order =  pd.DataFrame({
    'normalized_value':  normalized_values,
    'chord_label':empirical_ranking_triads
})

df_gt_intervals = pd.DataFrame({
    'normalized_value':normalized_values,
    'chord_label':empirical_ranking_intervals
})

In [36]:
df_ranking_periods_considered = joined_case_by_case[joined_case_by_case['periods_considered']==11]

w=250
h=250


triads_rank = df_ranking_periods_considered[df_ranking_periods_considered['ground_truth_type'].str.contains('Triads - Ranking Order')]
intervals = df_ranking_periods_considered[df_ranking_periods_considered['ground_truth_type'].str.contains('Intervals')]
triads = df_ranking_periods_considered[df_ranking_periods_considered['ground_truth_type'].str.contains('Triads - Numerical Ranking')]
# triads = triads[triads['']]
triads_chart = alt.Chart(triads).mark_line(
    opacity=0.8
).encode(
    x=alt.X('chord_label',title="Triad labels Ranked",sort=empirical_ranking_triads),
    y=alt.Y('normalized_value'),
    color=alt.Color('clean_subharmonic_method:N', title="Method to try"),
    shape=alt.Shape('method_focus:N', title='Method Focus')
)
ranking_emp_chart = triads_chart+ alt.Chart(df_gt_triads).mark_line(color='black',strokeDash=[5,5]).encode(
    x=alt.X('chord_label',sort=empirical_ranking_triads),
    y=alt.Y('normalized_value',title=None)
).properties(width=w,height=h)
ranking_rank =triads_chart+ alt.Chart(df_gt_triads_ranking_order).mark_line(color='black',strokeDash=[5,5]).encode(
    x=alt.X('chord_label',sort=empirical_ranking_triads),
    y=alt.Y('normalized_value',title=None)
).properties(width=w,height=h)

intervals_chart = alt.Chart(intervals).mark_line(
    opacity=0.8
).encode(
    x=alt.X('chord_label',title="Interval labels Ranked",sort=empirical_ranking_intervals),
    y=alt.Y('normalized_value'),
    color=alt.Color('clean_subharmonic_method:N', title="Method to try"),
    shape=alt.Shape('method_focus:N', title='Method Focus')
)

ranking_intervals_chart = intervals_chart+ alt.Chart(df_gt_intervals).mark_line(color='black',strokeDash=[5,5]).encode(
    x=alt.X('chord_label',sort=empirical_ranking_intervals),
    y=alt.Y('normalized_value', title='Normalized Score for Each Chord Label')
).properties(width=w,height=h)
(ranking_intervals_chart | ranking_rank | ranking_emp_chart ).configure_legend(
    orient='bottom',
    titleAnchor='middle',
    labelBaseline='middle',
    direction='horizontal',
    columns=3,

    
    # legendX=w/1.5,
    # legendY=h*1.4
).properties(
    title=f"Comparison of Normalized Scores Across Chord Labels for Each Method at 14 Period-Cycles Considered and Threshold Exponent {t_exp}"
).configure_title(
    anchor='middle'
)

alt.HConcatChart(...)

# Lets break down subharmonics

In [48]:
%reset -f

In [6]:
import pandas as pd
import altair as alt
import psychoacoustic_tension_chan_module.subharmonic_module as shm

triads_complete = pd.read_csv('../data_csvs/triad_subharmonic_w_threshholds.csv')
triads_complete['subharmonic_method'] = triads_complete['case']

In [7]:
droppable_indices = triads_complete[triads_complete['threshold_exponent'].isin(['10**1','10**2'])].index
triads_complete.drop(droppable_indices, inplace=True)
triads_complete.drop(['Unnamed: 0'], axis=1, inplace=True)
triads_complete 

t_values  mean_t_sub  \
20358   [0.00382225643297143, 0.003033726941295533, 0....    0.003136   
20359   [0.00382225643297143, 0.003033726941295533, 0....    0.003986   
20360   [0.00764451286594286, 0.006067453882591066, 0....    0.006271   
20361   [0.00382225643297143, 0.003033726941295533, 0....    0.003136   
20362   [0.00764451286594286, 0.009101180823886598, 0....    0.008133   
...                                                   ...         ...   
122143  [0.05733384649457145, 0.057640811884615124, 0....    0.057588   
122144  [0.07262287222645716, 0.07280944659109279, 0.0...    0.072556   
122145  [0.05733384649457145, 0.057640811884615124, 0....    0.057588   
122146  [0.07262287222645716, 0.07280944659109279, 0.0...    0.072556   
122147  [0.04586707719565716, 0.04550590411943299, 0.0...    0.045708   

                 indices  difference_(delta_t)  \
20358      [0.0, 0, 0.0]              0.001271   
20359      [0.0, 0, 1.0]              0.002068   
20360      [1.0, 1, 1.0]              0.002542   
20361      [0.0, 0, 0.0]              0.001271   
20362      [1.0, 2, 2.0]              0.001457   
...                  ...                   ...   
122143  [14.0, 18, 23.0]              0.000455   
122144  [18.0, 23, 29.0]              0.000573   
122145  [14.0, 18, 23.0]              0.000455   
122146  [18.0, 23, 29.0]              0.000573   
122147  [11.0, 14, 18.0]              0.000361   

        difference_ratio_(delta_t_hat)  \
20358                         0.405401   
20359                         0.518906   
20360                         0.405401   
20361                         0.405401   
20362                         0.179107   
...                                ...   
122143                        0.007902   
122144                        0.007902   
122145                        0.007902   
122146                        0.007902   
122147                        0.007902   

                                                     case  tension_score  \
20358   Smallest_delta_t_and_filter_by_smallest_t_sub_...    4669.130288   
20359   Smallest_delta_t_and_filter_by_smallest_t_sub_...    4669.130288   
20360   Smallest_delta_t_and_filter_by_smallest_t_sub_...    4669.130288   
20361           Smallest_delta_t_and_choose_top_3_delta_t       0.000000   
20362           Smallest_delta_t_and_choose_top_3_delta_t       0.000000   
...                                                   ...            ...   
122143      Smallest_ratio_and_filter_by_smallest_delta_t  986798.451886   
122144      Smallest_ratio_and_filter_by_smallest_delta_t  986798.451886   
122145              Smallest_ratio_and_choose_top_3_ratio  986798.451886   
122146              Smallest_ratio_and_choose_top_3_ratio  986798.451886   
122147              Smallest_ratio_and_choose_top_3_ratio  986798.451886   

       note_names chord_label  normalized_tension_score  periods_considered  \
20358    C4,E4,G4          CM                  0.746162                   4   
20359    C4,E4,G4          CM                  0.746162                   4   
20360    C4,E4,G4          CM                  0.746162                   4   
20361    C4,E4,G4          CM                  0.000000                   4   
20362    C4,E4,G4          CM                  0.000000                   4   
...           ...         ...                       ...                 ...   
122143  C4,E4,G#4        CAug                  0.036666                  32   
122144  C4,E4,G#4        CAug                  0.036666                  32   
122145  C4,E4,G#4        CAug                  0.041219                  32   
122146  C4,E4,G#4        CAug                  0.041219                  32   
122147  C4,E4,G#4        CAug                  0.041219                  32   

       threshold_exponent                                 subharmonic_method  
20358               10**3  Smallest_delta_t_and_filter_by_smallest_t_sub_...  
20359               10**3  Smallest_delta_t_an

Studying triads_complete

In [8]:
triads_complete[(triads_complete['chord_label']=='CM') & (14<=triads_complete['periods_considered']) & (triads_complete['periods_considered']<16)]

t_values  mean_t_sub  \
23868   [0.00382225643297143, 0.003033726941295533, 0....    0.003136   
23869   [0.01528902573188572, 0.015168634706477665, 0....    0.015255   
23870   [0.01911128216485715, 0.018202361647773196, 0....    0.018390   
23871   [0.01528902573188572, 0.015168634706477665, 0....    0.015255   
23872   [0.03057805146377144, 0.03033726941295533, 0.0...    0.030509   
...                                                   ...         ...   
115852  [0.03057805146377144, 0.03033726941295533, 0.0...    0.030509   
115853  [0.0382225643297143, 0.03943845023684193, 0.03...    0.038642   
115854  [0.01528902573188572, 0.015168634706477665, 0....    0.015255   
115855  [0.03057805146377144, 0.03033726941295533, 0.0...    0.030509   
115856  [0.0382225643297143, 0.03943845023684193, 0.03...    0.038642   

                indices  difference_(delta_t)  difference_ratio_(delta_t_hat)  \
23868     [0.0, 0, 0.0]              0.001271                        0.405401   
23869     [3.0, 4, 5.0]              0.000138                        0.009025   
23870     [4.0, 5, 6.0]              0.001254                        0.068184   
23871     [3.0, 4, 5.0]              0.000138                        0.009025   
23872    [7.0, 9, 11.0]              0.000275                        0.009025   
...                 ...                   ...                             ...   
115852   [7.0, 9, 11.0]              0.000275                        0.009025   
115853  [9.0, 12, 14.0]              0.001216                        0.031465   
115854    [3.0, 4, 5.0]              0.000138                        0.009025   
115855   [7.0, 9, 11.0]              0.000275                        0.009025   
115856  [9.0, 12, 14.0]              0.001216                        0.031465   

                                                     case  tension_score  \
23868   Smallest_delta_t_and_filter_by_smallest_t_sub_...       0.000000   
23869   Smallest_delta_t_and_filter_by_smallest_t_sub_...       0.000000   
23870   Smallest_delta_t_and_filter_by_smallest_t_sub_...       0.000000   
23871           Smallest_delta_t_and_choose_top_3_delta_t       0.000000   
23872           Smallest_delta_t_and_choose_top_3_delta_t       0.000000   
...                                                   ...            ...   
115852      Smallest_ratio_and_filter_by_smallest_delta_t  254780.752095   
115853      Smallest_ratio_and_filter_by_smallest_delta_t  254780.752095   
115854              Smallest_ratio_and_choose_top_3_ratio  254780.752095   
115855              Smallest_ratio_and_choose_top_3_ratio  254780.752095   
115856              Smallest_ratio_and_choose_top_3_ratio  254780.752095   

       note_names chord_label  normalized_tension_score  periods_considered  \
23868    C4,E4,G4          CM                  0.000000                  14   
23869    C4,E4,G4          CM                  0.000000                  14   
23870    C4,E4,G4          CM                  0.000000                  14   
23871    C4,E4,G4          CM                  0.000000                  14   
23872    C4,E4,G4          CM                  0.000000                  14   
...           ...         ...                       ...                 ...   
115852   C4,E4,G4          CM                  0.085104                  15   
115853   C4,E4,G4          CM                  0.085104                  15   
115854   C4,E4,G4          CM                  0.087470                  15   
115855   C4,E4,G4          CM                  0.087470                  15   
115856   C4,E4,G4          CM                  0.087470                  15   

       threshold_exponent                                 subharmonic_method  
23868               10**3  Smallest_delta_t_and_filter_by_smallest_t_sub_...  
23869               10**3  Smallest_delta_t_and_filter_by_smallest_t_sub_...  
23870               10**3  Smallest_delta_t_and_filter_by_smallest_t_sub_...  
23871               1

In [9]:
def take_period_def_extract_winners(period_df,observable_metrics):
    note_names = period_df.columns
    new_df = {
        'note_name':[],
        't_values':[],
        # 't_value_in_met':[],
        'cycle_or_t':[],
        'winner_num':[],
    }
    count=0
    for item in observable_metrics:
        print(item)
        indices = item['indices']
        print('indices:', indices)
        count+=1
        
        values = item['t_values']
        print('values:', values)
        for i in range(len(indices)):
            note_name = note_names[i]
            new_df['note_name'].append(note_name)
            new_df['t_values'].append(values[i])
            new_df['cycle_or_t'].append(indices[i])
            new_df['winner_num'].append(count)
            # new_df['t_value_in_met'].append(values[i])
    return pd.DataFrame(new_df)


In [10]:
chord_labels = triads_complete['chord_label'].unique()

In [11]:
def create_chart_for_all_harmonics(df_considered):


    chart3 = alt.Chart(df_considered).mark_bar(
        opacity=0.2,
        clip=True
        # xOffset=0.5
    ).encode(
        x=alt.X('t_values', title='Period',scale=alt.Scale(domain=[0, 0.08])),
        y=alt.Y('cycle_or_t:Q', title='Cycle' ),
        color=alt.Color('note_name', title='Note'),
    ).properties(
        width=600,
        height=300
    )
    return chart3


In [12]:
triads_complete = clean_subharmonic_method_names(triads_complete)
triads_complete = add_method_focus_column(triads_complete)


NameError: name 'clean_subharmonic_method_names' is not defined

In [13]:
eval(triads_complete.t_values.values[0])

[0.00382225643297143, 0.003033726941295533, 0.00255105010979403]

In [14]:
def extract_winners_from_methods(triads_df,long_period_df,note_array):
    
    ## triads df only contains the triad label we want to consider
    ## expected finished result
    ## note, winner number, t_values, mean_t_sub , cycle_or_tnum, method, focus, 
    final_winner_df = pd.DataFrame()


    for method in triads_df['subharmonic_method'].unique():
        print(f'Now processing method {method}')
        method_df = triads_df[triads_df['subharmonic_method'] == method]

       

        ## now that we have the method df, we need to take each row, extract the t_values and indices,
        ## pair them with each note in triad label. 
        for i, r in method_df.iterrows():
            t_values = eval(r['t_values'])
            indices = eval(r['indices'])


            ## getting min  t value and max t value
            min_t_value = min(t_values)
            max_t_value = max(t_values)
            min_cycle_for_t_sub = min(indices)
            max_cycle_for_t_sub = max(indices)
            periods_considered = r['periods_considered']

            for j in range(len(indices)):
                note_name = note_array[j]
                new_row = {
                    'Note Name':note_name,
                    'Period at Cycle number':t_values[j],
                    'Cycle number':indices[j],
                    'Method evaluation':method,
                    # 'clean_subharmonic_method':r['clean_subharmonic_method'],
                    'Method Focus':r['method_focus'],
                    'Ratio':r['difference_ratio_(delta_t_hat)'],
                    'delta_t':r['difference_(delta_t)'],
                    'T_sub':r['mean_t_sub'],
                    'min_t_value':min_t_value,
                    'max_t_value':max_t_value,
                    'min_cycle_for_t_sub':min_cycle_for_t_sub,
                    'periods_considered':periods_considered,
                    'max_cycle_for_t_sub':max_cycle_for_t_sub,
                    # 'chord_label':triad_label,
                    # 'periods_considered':r['periods_considered'],
                    # 'threshold_exponent':r['threshold_exponent'],
                }
                final_winner_df = pd.concat([final_winner_df,pd.DataFrame([new_row])], ignore_index=True)
    return final_winner_df
            


In [15]:
# def create_chart_for_winners():
    # 

In [16]:
### triads to consider CM, Cm, Cdim,Caug
periods_considered = 14
triads=['CM','Cm','Cdim','CAug']
threshold_considered = '10**7'

triads_complete = triads_complete[(triads_complete['periods_considered']>=periods_considered) & (triads_complete['periods_considered']<=periods_considered+1) & (triads_complete['threshold_exponent']==threshold_considered)]
# triads_complete[triads_complete['chord_label']=='CM']
triads_complete['difference_(delta_t)_with_c'] = triads_complete['difference_(delta_t)'] ** 2.1
triads_complete['difference_ratio_(delta_t_hat)_with_c'] = triads_complete['difference_(delta_t)_with_c']/triads_complete['mean_t_sub']



C:\Users\gabri\AppData\Local\Temp\ipykernel_4240\2818241683.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  triads_complete['difference_(delta_t)_with_c'] = triads_complete['difference_(delta_t)'] ** 2.1
C:\Users\gabri\AppData\Local\Temp\ipykernel_4240\2818241683.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  triads_complete['difference_ratio_(delta_t_hat)_with_c'] = triads_complete['difference_(delta_t)_with_c']/triads_complete['mean_t_sub']


In [17]:
triads_complete

t_values  mean_t_sub  \
64584  [0.00382225643297143, 0.003033726941295533, 0....    0.003136   
64585  [0.01528902573188572, 0.015168634706477665, 0....    0.015255   
64586  [0.01911128216485715, 0.018202361647773196, 0....    0.018390   
64587  [0.01528902573188572, 0.015168634706477665, 0....    0.015255   
64588  [0.03057805146377144, 0.03033726941295533, 0.0...    0.030509   
...                                                  ...         ...   
65281  [0.03057805146377144, 0.03033726941295533, 0.0...    0.030739   
65282  [0.03440030789674287, 0.033370996354250865, 0....    0.033827   
65283  [0.03440030789674287, 0.033370996354250865, 0....    0.033827   
65284  [0.02675579503080001, 0.027303542471659795, 0....    0.026849   
65285  [0.03057805146377144, 0.03033726941295533, 0.0...    0.030739   

               indices  difference_(delta_t)  difference_ratio_(delta_t_hat)  \
64584    [0.0, 0, 0.0]              0.001271                        0.405401   
64585    [3.0, 4, 5.0]              0.000138                        0.009025   
64586    [4.0, 5, 6.0]              0.001254                        0.068184   
64587    [3.0, 4, 5.0]              0.000138                        0.009025   
64588   [7.0, 9, 11.0]              0.000275                        0.009025   
...                ...                   ...                             ...   
65281   [7.0, 9, 12.0]              0.000965                        0.031395   
65282  [8.0, 10, 13.0]              0.001029                        0.030429   
65283  [8.0, 10, 13.0]              0.001029                        0.030429   
65284   [6.0, 8, 10.0]              0.000817                        0.030429   
65285   [7.0, 9, 12.0]              0.000965                        0.031395   

                                                    case  tension_score  \
64584  Smallest_delta_t_and_filter_by_smallest_t_sub_...   19827.678910   
64585  Smallest_delta_t_and_filter_by_smallest_t_sub_...   19827.678910   
64586  Smallest_delta_t_and_filter_by_smallest_t_sub_...   19827.678910   
64587          Smallest_delta_t_and_choose_top_3_delta_t  218383.384377   
64588          Smallest_delta_t_and_choose_top_3_delta_t  218383.384377   
...                                                  ...            ...   
65281      Smallest_ratio_and_filter_by_smallest_delta_t  129432.525619   
65282      Smallest_ratio_and_filter_by_smallest_delta_t  129432.525619   
65283              Smallest_ratio_and_choose_top_3_ratio  129432.525619   
65284              Smallest_ratio_and_choose_top_3_ratio  129432.525619   
65285              Smallest_ratio_and_choose_top_3_ratio  129432.525619   

      note_names chord_label  normalized_tension_score  periods_considered  \
64584   C4,E4,G4          CM                  0.042038                  14   
64585   C4,E4,G4          CM                  0.042038                  14   
64586   C4,E4,G4          CM                  0.042038                  14   
64587   C4,E4,G4          CM                  1.000000                  14   
64588   C4,E4,G4          CM                  1.000000                  14   
...          ...         ...                       ...                 ...   
65281  C4,E4,G#4        CAug                  0.019941                  15   
65282  C4,E4,G#4        CAug                  0.019941                  15   
65283  C4,E4,G#4        CAug                  0.022476                  15   
65284  C4,E4,G#4        CAug                  0.022476                  15   
65285  C4,E4,G#4        CAug                  0.022476                  15   

      threshold_exponent                                 subharmonic_method  \
64584              10**7  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
64585              10**7  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
64586              10**7  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
64587              10**7          Smallest_delta_t_and_choose_top_3_

## Difference ratio computation as periods_considered varies

In [18]:
## we first sum the difference ratios grouped by method, chord label and periods_considered
triads_to_consider = triads_complete[triads_complete['chord_label'].isin(triads)]
triads_to_consider

t_values  mean_t_sub  \
64584  [0.00382225643297143, 0.003033726941295533, 0....    0.003136   
64585  [0.01528902573188572, 0.015168634706477665, 0....    0.015255   
64586  [0.01911128216485715, 0.018202361647773196, 0....    0.018390   
64587  [0.01528902573188572, 0.015168634706477665, 0....    0.015255   
64588  [0.03057805146377144, 0.03033726941295533, 0.0...    0.030509   
...                                                  ...         ...   
65281  [0.03057805146377144, 0.03033726941295533, 0.0...    0.030739   
65282  [0.03440030789674287, 0.033370996354250865, 0....    0.033827   
65283  [0.03440030789674287, 0.033370996354250865, 0....    0.033827   
65284  [0.02675579503080001, 0.027303542471659795, 0....    0.026849   
65285  [0.03057805146377144, 0.03033726941295533, 0.0...    0.030739   

               indices  difference_(delta_t)  difference_ratio_(delta_t_hat)  \
64584    [0.0, 0, 0.0]              0.001271                        0.405401   
64585    [3.0, 4, 5.0]              0.000138                        0.009025   
64586    [4.0, 5, 6.0]              0.001254                        0.068184   
64587    [3.0, 4, 5.0]              0.000138                        0.009025   
64588   [7.0, 9, 11.0]              0.000275                        0.009025   
...                ...                   ...                             ...   
65281   [7.0, 9, 12.0]              0.000965                        0.031395   
65282  [8.0, 10, 13.0]              0.001029                        0.030429   
65283  [8.0, 10, 13.0]              0.001029                        0.030429   
65284   [6.0, 8, 10.0]              0.000817                        0.030429   
65285   [7.0, 9, 12.0]              0.000965                        0.031395   

                                                    case  tension_score  \
64584  Smallest_delta_t_and_filter_by_smallest_t_sub_...   19827.678910   
64585  Smallest_delta_t_and_filter_by_smallest_t_sub_...   19827.678910   
64586  Smallest_delta_t_and_filter_by_smallest_t_sub_...   19827.678910   
64587          Smallest_delta_t_and_choose_top_3_delta_t  218383.384377   
64588          Smallest_delta_t_and_choose_top_3_delta_t  218383.384377   
...                                                  ...            ...   
65281      Smallest_ratio_and_filter_by_smallest_delta_t  129432.525619   
65282      Smallest_ratio_and_filter_by_smallest_delta_t  129432.525619   
65283              Smallest_ratio_and_choose_top_3_ratio  129432.525619   
65284              Smallest_ratio_and_choose_top_3_ratio  129432.525619   
65285              Smallest_ratio_and_choose_top_3_ratio  129432.525619   

      note_names chord_label  normalized_tension_score  periods_considered  \
64584   C4,E4,G4          CM                  0.042038                  14   
64585   C4,E4,G4          CM                  0.042038                  14   
64586   C4,E4,G4          CM                  0.042038                  14   
64587   C4,E4,G4          CM                  1.000000                  14   
64588   C4,E4,G4          CM                  1.000000                  14   
...          ...         ...                       ...                 ...   
65281  C4,E4,G#4        CAug                  0.019941                  15   
65282  C4,E4,G#4        CAug                  0.019941                  15   
65283  C4,E4,G#4        CAug                  0.022476                  15   
65284  C4,E4,G#4        CAug                  0.022476                  15   
65285  C4,E4,G#4        CAug                  0.022476                  15   

      threshold_exponent                                 subharmonic_method  \
64584              10**7  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
64585              10**7  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
64586              10**7  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
64587              10**7          Smallest_delta_t_and_choose_top_3_

Make big graph comparing the selection of each triad

In [19]:
period_df_for_every_triad = pd.DataFrame()
df_winners_for_each_triad = pd.DataFrame()
df_aggregate_data_for_each_triad = pd.DataFrame()
for triad in triads:

    t_df= triads_complete[triads_complete['chord_label']==triad]
    notes = triads_complete[triads_complete['chord_label']==triad]['note_names'].values[0]
    note_arr = notes.split(',')

    period_df = shm.create_period_dataframe(note_arr, periods_considered=periods_considered)
    long_period_df = period_df.reset_index().melt(id_vars='index')
    long_period_df.columns = ['cycle_or_t', 'note_name', 't_values']
    # long_period_df['cycle_or_t'] = long_period_df['cycle_or_t'] 

    # chart = create_chart_for_all_harmonics(long_period_df)
    long_period_df['chord_label'] = triad

    ## after creating chart we need to extract winners for each method
    # triads complete has an indices that represents cycle_or_t

    extracted_winners_df = extract_winners_from_methods(t_df,long_period_df,note_array=note_arr)
    extracted_winners_df['Chord Label'] = triad


    # relevant_data

    period_df_for_every_triad = pd.concat([period_df_for_every_triad,long_period_df], ignore_index=True)
    df_winners_for_each_triad = pd.concat([df_winners_for_each_triad,extracted_winners_df], ignore_index=True)

#     # chart2 = create_chart_for_winners(extracted_winners_df)
# # long_period_df[long_period_df['cycle_or_t']==3]
# extracted_winners_df
# # chart
relevant_data = df_winners_for_each_triad[['Chord Label','Ratio','delta_t','T_sub','Method evaluation','min_t_value','max_t_value','min_cycle_for_t_sub']].drop_duplicates()

Now processing method Smallest_delta_t_and_filter_by_smallest_t_sub_(Chan's_method?)


KeyError: 'method_focus'

3 notas * 4 acordes * 3 candidatos * 6 metodos * 2  periodos distintos = 432

In [ ]:
df_winners_for_each_triad

Note Name  Period at Cycle number  Cycle number  \
0          C4                0.003822           0.0   
1          E4                0.003034           0.0   
2          G4                0.002551           0.0   
3          C4                0.015289           3.0   
4          E4                0.015169           4.0   
..        ...                     ...           ...   
643        E4                0.027304           8.0   
644       G#4                0.026487          10.0   
645        C4                0.030578           7.0   
646        E4                0.030337           9.0   
647       G#4                0.031302          12.0   

                                     Method evaluation           Method Focus  \
0    Smallest_delta_t_and_filter_by_smallest_t_sub_...        Delta_t focused   
1    Smallest_delta_t_and_filter_by_smallest_t_sub_...        Delta_t focused   
2    Smallest_delta_t_and_filter_by_smallest_t_sub_...        Delta_t focused   
3    Smallest_delta_t_and_filter_by_smallest_t_sub_...        Delta_t focused   
4    Smallest_delta_t_and_filter_by_smallest_t_sub_...        Delta_t focused   
..                                                 ...                    ...   
643              Smallest_ratio_and_choose_top_3_ratio  Delta_t/T_sub focused   
644              Smallest_ratio_and_choose_top_3_ratio  Delta_t/T_sub focused   
645              Smallest_ratio_and_choose_top_3_ratio  Delta_t/T_sub focused   
646              Smallest_ratio_and_choose_top_3_ratio  Delta_t/T_sub focused   
647              Smallest_ratio_and_choose_top_3_ratio  Delta_t/T_sub focused   

        Ratio   delta_t     T_sub  min_t_value  max_t_value  \
0    0.405401  0.001271  0.003136     0.002551     0.003822   
1    0.405401  0.001271  0.003136     0.002551     0.003822   
2    0.405401  0.001271  0.003136     0.002551     0.003822   
3    0.009025  0.000138  0.015255     0.015169     0.015306   
4    0.009025  0.000138  0.015255     0.015169     0.015306   
..        ...       ...       ...          ...          ...   
643  0.030429  0.000817  0.026849     0.026487     0.027304   
644  0.030429  0.000817  0.026849     0.026487     0.027304   
645  0.031395  0.000965  0.030739     0.030337     0.031302   
646  0.031395  0.000965  0.030739     0.030337     0.031302   
647  0.031395  0.000965  0.030739     0.030337     0.031302   

     min_cycle_for_t_sub  periods_considered  max_cycle_for_t_sub Chord Label  
0                    0.0                  14                  0.0          CM  
1                    0.0                  14                  0.0          CM  
2                    0.0                  14                  0.0          CM  
3                    3.0                  14                  5.0          CM  
4                    3.0                  14                  5.0          CM  
..                   ...                 ...                  ...         ...  
643                  6.0                  15                 10.0        CAug  
644                  6.0                  15                 10.0        CAug  
645                  7.0                  15                 12.0        CAug  
646                  7.0                  15                 12.0        CAug  
647                  7.0                  15                 12.0        CAug  

[648 rows x 14 columns]

In [20]:
period_df_for_every_triad

Empty DataFrame
Columns: []
Index: []

In [21]:
### computing min max t_values for ploting
# relevant_data
period_df_for_every_triad['Chord Label'] = period_df_for_every_triad['chord_label']
# period_df_for_every_triad['Period at Cycle number'] = period_df_for_every_triad['t_values']
period_df_for_every_triad['Cycle number'] = period_df_for_every_triad['cycle_or_t']
period_df_for_every_triad['Note Name'] = period_df_for_every_triad['note_name']

KeyError: 'chord_label'

## Need a a join dataframe
Want a dataframe that contains (each note is repeated (4 chords times 6 methods * three options) and that is repeated two periods.)

In [ ]:

## this returns a dataframe with all periods, and each period has an information on
# which method uses that period as winner. 
period_used_on_winner_df = pd.merge(period_df_for_every_triad,df_winners_for_each_triad,how='right', on=['Chord Label','Cycle number', 'Note Name'])
period_used_on_winner_df
# period_used_on_winner_df[period_used_on_winner_df['periods_considered']==15]
# period_used_on_winner_df[period_used_on_winner_df['Chord Label']=='CM']

cycle_or_t note_name  t_values chord_label Chord Label  Cycle number  \
0           0.0        C4  0.003822          CM          CM           0.0   
1           0.0        E4  0.003034          CM          CM           0.0   
2           0.0        G4  0.002551          CM          CM           0.0   
3           3.0        C4  0.015289          CM          CM           3.0   
4           4.0        E4  0.015169          CM          CM           4.0   
..          ...       ...       ...         ...         ...           ...   
643         8.0        E4  0.027304        CAug        CAug           8.0   
644        10.0       G#4  0.026487        CAug        CAug          10.0   
645         7.0        C4  0.030578        CAug        CAug           7.0   
646         9.0        E4  0.030337        CAug        CAug           9.0   
647        12.0       G#4  0.031302        CAug        CAug          12.0   

    Note Name  Period at Cycle number  \
0          C4                0.003822   
1          E4                0.003034   
2          G4                0.002551   
3          C4                0.015289   
4          E4                0.015169   
..        ...                     ...   
643        E4                0.027304   
644       G#4                0.026487   
645        C4                0.030578   
646        E4                0.030337   
647       G#4                0.031302   

                                     Method evaluation           Method Focus  \
0    Smallest_delta_t_and_filter_by_smallest_t_sub_...        Delta_t focused   
1    Smallest_delta_t_and_filter_by_smallest_t_sub_...        Delta_t focused   
2    Smallest_delta_t_and_filter_by_smallest_t_sub_...        Delta_t focused   
3    Smallest_delta_t_and_filter_by_smallest_t_sub_...        Delta_t focused   
4    Smallest_delta_t_and_filter_by_smallest_t_sub_...        Delta_t focused   
..                                                 ...                    ...   
643              Smallest_ratio_and_choose_top_3_ratio  Delta_t/T_sub focused   
644              Smallest_ratio_and_choose_top_3_ratio  Delta_t/T_sub focused   
645              Smallest_ratio_and_choose_top_3_ratio  Delta_t/T_sub focused   
646              Smallest_ratio_and_choose_top_3_ratio  Delta_t/T_sub focused   
647              Smallest_ratio_and_choose_top_3_ratio  Delta_t/T_sub focused   

        Ratio   delta_t     T_sub  min_t_value  max_t_value  \
0    0.405401  0.001271  0.003136     0.002551     0.003822   
1    0.405401  0.001271  0.003136     0.002551     0.003822   
2    0.405401  0.001271  0.003136     0.002551     0.003822   
3    0.009025  0.000138  0.015255     0.015169     0.015306   
4    0.009025  0.000138  0.015255     0.015169     0.015306   
..        ...       ...       ...          ...          ...   
643  0.030429  0.000817  0.026849     0.026487     0.027304   
644  0.030429  0.000817  0.026849     0.026487     0.027304   
645  0.031395  0.000965  0.030739     0.030337     0.031302   
646  0.031395  0.000965  0.030739     0.030337     0.031302   
647  0.031395  0.000965  0.030739     0.030337     0.031302   

     min_cycle_for_t_sub  periods_considered  max_cycle_for_t_sub  
0                    0.0                  14                  0.0  
1                    0.0                  14                  0.0  
2                    0.0                  14                  0.0  
3                    3.0                  14                  5.0  
4                    3.0                  14                  5.0  
..                   ...                 ...                  ...  
643                  6.0                  15                 10.0  
644                  6.0                  15                 10.0  
645                  7.0                  15                 12.0  
646                  7.0                  15                 12.0  
647                  7.0                  15                 12.0  

[648 rows x 18 columns]

 getting the rows that are in periods_considered 14 but not in periods_considered 15

In [22]:
# period_used_on_winner_df[period_used_on_winner_df['Chord Label']=='CM']

period_used_on_winner_df.to_csv('../data_csvs/parameters_each_method_used_for_tension_subharmonic.csv',index=False)

## Ok now plot, layer three different charts 
First plot all subharmonics for each chord with lesser opacity. Layer the winners with same color, and put on top the relevant data, where rectangles x and 

In [23]:
period_used_on_winner_df = pd.read_csv('../data_csvs/parameters_each_method_used_for_tension_subharmonic.csv')

In [24]:


## chart for all periods
chart_for_all_harms= alt.Chart(period_df_for_every_triad).mark_bar(
    opacity=0.2,
    clip=True
    # xOffset=0.5
).encode(
    x=alt.X('Period at Cycle number', title='Period',scale=alt.Scale(domain=[0, 0.08])),
    y=alt.Y('Cycle number:Q', title='Cycle', scale=alt.Scale(reverse=True) ),
    y2=alt.Y2(datum=period_df_for_every_triad['Cycle number'].max()+1),
    color=alt.Color('Note Name', title='Note'),
)
# ).properties(
#     width=600,
#     height=300
# )
chart_for_all_harms


KeyError: 'Cycle number'

In [25]:
df_winners_for_each_triad

Empty DataFrame
Columns: []
Index: []

In [26]:


chart_for_winners = alt.Chart(df_winners_for_each_triad).mark_bar(
    opacity=0.8,
    clip=True
).encode(
    x=alt.X('Period at Cycle number', title='Period',scale=alt.Scale(domain=[0, 0.08])),
    y=alt.Y('Cycle number:Q', title='Cycle', scale=alt.Scale(reverse=True) ),
    y2=alt.Y2(datum=df_winners_for_each_triad['Cycle number'].max()+1),
    color=alt.Color('Note Name', title='Note'),
    tooltip=['Method evaluation','Chord Label','Note Name','Period at Cycle number','Cycle number','Ratio','delta_t','T_sub','min_t_value','max_t_value','Method Focus']
)
# ).properties(
#     width=600,
#     height=300
    
# )
chart_for_winners



KeyError: 'Cycle number'

In [27]:
relevant_data

NameError: name 'relevant_data' is not defined

In [ ]:
## do i have to join all tables?
# period_df_for_every_triad.drop(['cycle_or_t','note_name','t_values','chord_label'], axis=1, inplace=True)
period_df_for_every_triad

cycle_or_t note_name  t_values chord_label Chord Label  Cycle number  \
0             0        C4  0.003822          CM          CM             0   
1             1        C4  0.007645          CM          CM             1   
2             2        C4  0.011467          CM          CM             2   
3             3        C4  0.015289          CM          CM             3   
4             4        C4  0.019111          CM          CM             4   
..          ...       ...       ...         ...         ...           ...   
163           9       G#4  0.024079        CAug        CAug             9   
164          10       G#4  0.026487        CAug        CAug            10   
165          11       G#4  0.028894        CAug        CAug            11   
166          12       G#4  0.031302        CAug        CAug            12   
167          13       G#4  0.033710        CAug        CAug            13   

    Note Name  
0          C4  
1          C4  
2          C4  
3          C4  
4          C4  
..        ...  
163       G#4  
164       G#4  
165       G#4  
166       G#4  
167       G#4  

[168 rows x 7 columns]

In [28]:
df_winners_for_each_triad

Empty DataFrame
Columns: []
Index: []

In [29]:
relevant_data

NameError: name 'relevant_data' is not defined

In [30]:
# period_df_for_every_triad.join(df_winners_for_each_triad, how='left',on=['Chord Label','Note Name','Period at Cycle number','Cycle number'],lsuffix='_winner')

## this returns a dataframe with all periods, and each period has an information on
# which method uses that period as winner. 
period_used_on_winner_df = pd.merge(period_df_for_every_triad,df_winners_for_each_triad,how='left', on=['Chord Label','Cycle number', 'Note Name'])
period_used_on_winner_df

KeyError: 'Chord Label'

In [31]:
## dropna?
period_used_on_winner_df = period_used_on_winner_df.dropna(subset=['Method evaluation'])
period_used_on_winner_df

cycle_or_t note_name  t_values chord_label Chord Label  Cycle number  \
0             0        C4  0.003822          CM          CM             0   
1             0        C4  0.003822          CM          CM             0   
2             0        C4  0.003822          CM          CM             0   
3             0        C4  0.003822          CM          CM             0   
4             0        C4  0.003822          CM          CM             0   
..          ...       ...       ...         ...         ...           ...   
635          13       G#4  0.033710        CAug        CAug            13   
636          13       G#4  0.033710        CAug        CAug            13   
637          13       G#4  0.033710        CAug        CAug            13   
638          13       G#4  0.033710        CAug        CAug            13   
639          13       G#4  0.033710        CAug        CAug            13   

    Note Name  Period at Cycle number  \
0          C4                0.003822   
1          C4                0.003822   
2          C4                0.003822   
3          C4                0.003822   
4          C4                0.003822   
..        ...                     ...   
635       G#4                0.033710   
636       G#4                0.033710   
637       G#4                0.033710   
638       G#4                0.033710   
639       G#4                0.033710   

                                     Method evaluation           Method Focus  \
0    Smallest_delta_t_and_filter_by_smallest_t_sub_...        Delta_t focused   
1                Smallest_t_sub_and_choose_top_3_t_sub          T_sub focused   
2                Smallest_t_sub_and_choose_top_3_t_sub          T_sub focused   
3                Smallest_t_sub_and_choose_top_3_t_sub          T_sub focused   
4                Smallest_t_sub_and_choose_top_3_t_sub          T_sub focused   
..                                                 ...                    ...   
635      Smallest_delta_t_and_filter_by_smallest_ratio        Delta_t focused   
636      Smallest_delta_t_and_filter_by_smallest_ratio        Delta_t focused   
637      Smallest_ratio_and_filter_by_smallest_delta_t  Delta_t/T_sub focused   
638              Smallest_ratio_and_choose_top_3_ratio  Delta_t/T_sub focused   
639              Smallest_ratio_and_choose_top_3_ratio  Delta_t/T_sub focused   

        Ratio   delta_t     T_sub  min_t_value  max_t_value  \
0    0.405401  0.001271  0.003136     0.002551     0.003822   
1    0.405401  0.001271  0.003136     0.002551     0.003822   
2    0.518906  0.002068  0.003986     0.003034     0.005102   
3    0.405401  0.001271  0.003136     0.002551     0.003822   
4    0.518906  0.002068  0.003986     0.003034     0.005102   
..        ...       ...       ...          ...          ...   
635  0.030429  0.001029  0.033827     0.033371     0.034400   
636  0.030429  0.001029  0.033827     0.033371     0.034400   
637  0.030429  0.001029  0.033827     0.033371     0.034400   
638  0.030429  0.001029  0.033827     0.033371     0.034400   
639  0.030429  0.001029  0.033827     0.033371     0.034400   

     min_cycle_for_t_sub  periods_considered  max_cycle_for_t_sub  \
0                    0.0                14.0                  0.0   
1                    0.0                14.0                  0.0   
2                    0.0                14.0                  1.0   
3                    0.0                15.0                  0.0   
4                    0.0                15.0                  1.0   
..                   ...                 ...                  ...   
635                  8.0                14.0                 13.0   
636                  8.0                15.0                 13.0   
637                  8.0                15.0                 13.0   
638                  8.0                14.0                 13.0   
639                  8.0                15.0                 13.0   

                            

In [32]:
period_used_on_winner_df['subharmonic_method']=period_used_on_winner_df['Method evaluation']

In [33]:
period_used_on_winner_df = clean_subharmonic_method_names(period_used_on_winner_df)
period_used_on_winner_df.to_csv('../data_csvs/parameters_each_method_used_for_tension_subharmonic.csv',index=False)

NameError: name 'clean_subharmonic_method_names' is not defined

In [34]:
period_used_on_winner_df

cycle_or_t note_name  t_values chord_label Chord Label  Cycle number  \
0             0        C4  0.003822          CM          CM             0   
1             0        C4  0.003822          CM          CM             0   
2             0        C4  0.003822          CM          CM             0   
3             0        C4  0.003822          CM          CM             0   
4             0        C4  0.003822          CM          CM             0   
..          ...       ...       ...         ...         ...           ...   
635          13       G#4  0.033710        CAug        CAug            13   
636          13       G#4  0.033710        CAug        CAug            13   
637          13       G#4  0.033710        CAug        CAug            13   
638          13       G#4  0.033710        CAug        CAug            13   
639          13       G#4  0.033710        CAug        CAug            13   

    Note Name  Period at Cycle number  \
0          C4                0.003822   
1          C4                0.003822   
2          C4                0.003822   
3          C4                0.003822   
4          C4                0.003822   
..        ...                     ...   
635       G#4                0.033710   
636       G#4                0.033710   
637       G#4                0.033710   
638       G#4                0.033710   
639       G#4                0.033710   

                                     Method evaluation           Method Focus  \
0    Smallest_delta_t_and_filter_by_smallest_t_sub_...        Delta_t focused   
1                Smallest_t_sub_and_choose_top_3_t_sub          T_sub focused   
2                Smallest_t_sub_and_choose_top_3_t_sub          T_sub focused   
3                Smallest_t_sub_and_choose_top_3_t_sub          T_sub focused   
4                Smallest_t_sub_and_choose_top_3_t_sub          T_sub focused   
..                                                 ...                    ...   
635      Smallest_delta_t_and_filter_by_smallest_ratio        Delta_t focused   
636      Smallest_delta_t_and_filter_by_smallest_ratio        Delta_t focused   
637      Smallest_ratio_and_filter_by_smallest_delta_t  Delta_t/T_sub focused   
638              Smallest_ratio_and_choose_top_3_ratio  Delta_t/T_sub focused   
639              Smallest_ratio_and_choose_top_3_ratio  Delta_t/T_sub focused   

        Ratio   delta_t     T_sub  min_t_value  max_t_value  \
0    0.405401  0.001271  0.003136     0.002551     0.003822   
1    0.405401  0.001271  0.003136     0.002551     0.003822   
2    0.518906  0.002068  0.003986     0.003034     0.005102   
3    0.405401  0.001271  0.003136     0.002551     0.003822   
4    0.518906  0.002068  0.003986     0.003034     0.005102   
..        ...       ...       ...          ...          ...   
635  0.030429  0.001029  0.033827     0.033371     0.034400   
636  0.030429  0.001029  0.033827     0.033371     0.034400   
637  0.030429  0.001029  0.033827     0.033371     0.034400   
638  0.030429  0.001029  0.033827     0.033371     0.034400   
639  0.030429  0.001029  0.033827     0.033371     0.034400   

     min_cycle_for_t_sub  periods_considered  max_cycle_for_t_sub  \
0                    0.0                14.0                  0.0   
1                    0.0                14.0                  0.0   
2                    0.0                14.0                  1.0   
3                    0.0                15.0                  0.0   
4                    0.0                15.0                  1.0   
..                   ...                 ...                  ...   
635                  8.0                14.0                 13.0   
636                  8.0                15.0                 13.0   
637                  8.0                15.0                 13.0   
638                  8.0                14.0                 13.0   
639                  8.0                15.0                 13.0   

                            

In [46]:
# ## now lets see charts
# chart_for_all_harms= alt.Chart(period_used_on_winner_df).mark_bar(
#     opacity=0.4,
#     clip=True
#     # xOffset=0.5
# ).encode(
#     x=alt.X('t_values', title='Period',scale=alt.Scale(domain=[0, 0.08])),
#     y=alt.Y('Cycle number:Q', title='Cycle', scale=alt.Scale(reverse=True, domain=[0, periods_considered]) ),
#     y2=alt.Y2(datum=periods_considered+1),
#     color=alt.Color('Note Name', title='Note'),
# )



### if delta_t same delta t is present on both periods considered then text color is purple
## if only on periods 14 then blue
## if only on periods 15 then red

text_color = alt.datum.periods_considered == periods_considered

## chart for t_subs_with_difference

t_subs = alt.Chart(period_used_on_winner_df).mark_rect().encode(
    x=alt.X('min_t_value',title='T_sub in Seconds'),
    x2=alt.X2('max_t_value'),
    y=alt.Y('min_cycle_for_t_sub', scale=alt.Scale(reverse=True, domain=[0, periods_considered+1])),
    y2=alt.Y2(datum=periods_considered+1),
    color=alt.Color('delta_t', scale=alt.Scale(domain=[0,0.00175],range=['lightgreen', 'red']), legend=None)

).properties(
    width=100,
    height=100,
)

text_chart = alt.Chart(period_used_on_winner_df).mark_text(
    opacity=0.6
).encode(
    x=alt.X('min_t_value',title='T_sub in Seconds'),
    x2=alt.X2('max_t_value'),
    y=alt.Y('max_cycle_for_t_sub', title=None,scale=alt.Scale(reverse=True, domain=[0, periods_considered+1])),
    # y2=alt.Y2(datum=periods_considered),
    text=alt.Text('delta_t:Q',format='.3s'),
    color=alt.Color('periods_considered:N',legend=None)
).properties(
    width=100,
    height=100,
)


facet_chart = (t_subs + text_chart).facet(
    
    row=alt.Row('Chord Label:N', title='Cycle Numbers Chosen for each Chord Label Candidate',sort=triads ,),
    column=alt.Column('clean_subharmonic_method:N', title='Subharmonic Method')    
    
).resolve_scale(color='shared',).resolve_legend(color='shared',fill='shared').properties(
    title=f'T_sub and delta_t Values Chosen for each Method and Chord for Different Triads at {periods_considered} Periods Considered'
).configure_title(
    anchor='middle'
).configure_facet(
    spacing=5
)
facet_chart


alt.FacetChart(...)

In [43]:
## chart for t_subs_with_difference

t_subs = alt.Chart(period_used_on_winner_df).mark_rect().encode(
    x=alt.X('T_sub'),
    # x2=alt.X2('max_t_value'),
    y=alt.Y('min_cycle_for_t_sub', scale=alt.Scale(reverse=True, domain=[0, periods_considered])),
    y2=alt.Y2(datum=periods_considered),
    color=alt.Color('delta_t:Q', 
                    scale=alt.Scale(domain=[0,.00175],range=['lightgreen', 'red']),
                    title='Delta t',
                    )
).properties(
    width=400,
    height=400,
)

text_chart = alt.Chart(period_used_on_winner_df).mark_text().encode(
    x=alt.X('min_t_value'),
    x2=alt.X2('max_t_value'),
    y=alt.Y('max_cycle_for_t_sub', scale=alt.Scale(reverse=True, domain=[0, periods_considered])),
    y2=alt.Y2(datum=periods_considered),
    text=alt.Text('delta_t:Q', format='.3s'),
    color=alt.Color('periods_considered:N',     
                    title='Period-Cycles Considered',
                    )
).properties(
    width=400,
    height=400,
)

(t_subs + text_chart).configure_legend(
    orient='bottom'
)


alt.LayerChart(...)

In [37]:
## chart for t_subs
t_sub_chart = alt.Chart(relevant_data).mark_rect().encode(
    
    x=alt.X('min_t_value', title='Min T Value', scale=alt.Scale(domain=[0, 0.08])),
    x2=alt.X2('max_t_value'),
    y=alt.Y('min_cycle_for_t_sub', title='Cycle',scale=alt.Scale(reverse=True)),
    y2=alt.Y2(datum=period_df_for_every_triad['cycle_or_t'].max()+1),
    color=alt.Color('delta_t',scale=alt.Scale(range=['lightgreen','red']))
)

(t_sub_chart + chart_for_all_harms + chart_for_winners)


NameError: name 'relevant_data' is not defined

In [38]:
Other graphs. 

SyntaxError: invalid syntax (3491642211.py, line 1)